Import necessary libraries and set pandas standards

In [1]:
import os
import geopandas as gp
import pandas as pd
import numpy as np
max_rows = 9999
max_cols = 9999
pd.set_option("display.max_rows", max_rows, "display.max_columns", max_cols) 

### Import the data

In [2]:
#Set working directory and necessary file paths
wd = os.path.join(os.getcwd())
source_files = os.path.join(wd,'raw-from-source')

#Prec shapefile shapefile
prec = gp.read_file(os.path.join(os.path.join(source_files,'SBE_PRECINCTS_20200127'),'PRECINCTS_20200127.shp'))
#Unsorted results
unsorted = pd.read_csv(os.path.join(os.path.join(source_files,'results_pct_20200303'),'results_pct_20200303.txt'), delimiter = '\t')
#Sorted results (used for certain counties)
pct_sorted = os.path.join(source_files,'pct_sorted')

In [3]:
#Read in the county-specific filed into a sorted data dictionary with the keys as the county name and value as the dataframe
dfs = []
names = []

for i in os.listdir(pct_sorted):
    path = os.path.join(pct_sorted,i)
    co_df= pd.read_csv(path,delimiter = '\t')
    dfs.append(co_df)
    co_name = str(i.replace('_PRECINCT_SORT.txt',''))
    co_name = str(co_name.replace('_',' '))
    names.append(co_name)
sorted_dict = dict(zip(names,dfs))

## Clean the data

### Drop sorted counties from unsorted and concatenate all back together

In [4]:
unsorted_drop = unsorted[~unsorted['County'].isin(names)]
unsorted_drop.head()

County Election Date  Precinct  Contest Group ID Contest Type  \
0       ROWAN    03/03/2020        24              2864            S   
1   BRUNSWICK    03/03/2020        06              1032            S   
4    COLUMBUS    03/03/2020       P03              1027            S   
8  CUMBERLAND    03/03/2020  ABSENTEE              2447            S   
9    CARTERET    03/03/2020      ATSL              2450            S   

                           Contest Name                    Choice  \
0         PRESIDENTIAL PREFERENCE (LIB)            Vermin Supreme   
1  NC COMMISSIONER OF AGRICULTURE (DEM)  Donovan Alexander Watson   
4                      NC AUDITOR (DEM)            Luis A. Toledo   
8          NC LIEUTENANT GOVERNOR (DEM)              Chaz Beasley   
9          NC LIEUTENANT GOVERNOR (REP)             Greg Gebhardt   

  Choice Party  Vote For  Election Day  One Stop  Absentee by Mail  \
0          LIB         1             0         0                 0   
1          DEM         1             8        11                 0   
4          DEM         1             8         0                 0   
8          DEM         1             0         0                36   
9          REP         1             5         0                 0   

   Provisional  Total Votes Real Precinct  
0            0            0             Y  
1            3           22             Y  
4            0            8             Y  
8            0           36             N  
9            0            5             Y

In [5]:
count = 0
for k,v in sorted_dict.items():
    if count == 0:
        sorted_concat = v
        count = 1
    else:
        sorted_concat = pd.concat([sorted_concat,v])
sorted_concat.head()

county_id     county election_dt result_type_lbl result_type_desc  \
0          3  ALLEGHANY  03/03/2020             STD         <NORMAL>   
1          3  ALLEGHANY  03/03/2020             STD         <NORMAL>   
2          3  ALLEGHANY  03/03/2020             STD         <NORMAL>   
3          3  ALLEGHANY  03/03/2020             STD         <NORMAL>   
4          3  ALLEGHANY  03/03/2020             STD         <NORMAL>   

   contest_id                            contest_title contest_party_lbl  \
0         627  ALLEGHANY COUNTY BOARD OF COMMISSIONERS               REP   
1         627  ALLEGHANY COUNTY BOARD OF COMMISSIONERS               REP   
2         627  ALLEGHANY COUNTY BOARD OF COMMISSIONERS               REP   
3         627  ALLEGHANY COUNTY BOARD OF COMMISSIONERS               REP   
4         627  ALLEGHANY COUNTY BOARD OF COMMISSIONERS               REP   

   contest_vote_for precinct_code  \
0                 2            01   
1                 2            01   
2                 2            01   
3                 2            01   
4                 2            01   

                                       precinct_name  candidate_id  \
0  CHERRY LANE                                   ...          1309   
1  CHERRY LANE                                   ...          1309   
2  CHERRY LANE                                   ...          1309   
3  CHERRY LANE                                   ...          1309   
4  CHERRY LANE                                   ...          1309   

                candidate_name candidate_party_lbl  group_num    group_name  \
0  Christopher (Chris) Johnson                 REP          2  ELECTION DAY   
1  Christopher (Chris) Johnson                 REP          3      ONE STOP   
2  Christopher (Chris) Johnson                 REP          4          MAIL   
3  Christopher (Chris) Johnson                 REP          5   PROVISIONAL   
4  Christopher (Chris) Johnson                 REP          6      TRANSFER   

  voting_method_lbl voting_method_rslt_desc  vote_ct  precinct_cd  
0                 V            Election Day       72          NaN  
1                 O      Absentee: One-Stop       56          NaN  
2                 M       Absentee: By-Mail        4          NaN  
3                 P             Provisional        2          NaN  
4                 T  Election Day: Transfer        0          NaN

In [6]:
# Reset the sorted data columns
sorted_concat.columns = ["county_id","County","Election Date","result_type_lbl","result_type_desc","contest_id","Contest Name","Choice Party","contest_vote_for","Precinct","Precinct Name","candidate_id","Choice","Choice Party","group_num","group_name","voting_method","voting method_rslt","Total Votes","precinct_cd"]

In [7]:
print(sorted_concat['County'].unique())

['ALLEGHANY' 'AVERY' 'BEAUFORT' 'BERTIE' 'BLADEN' 'BUNCOMBE' 'CABARRUS'
 'CALDWELL' 'CAMDEN' 'CURRITUCK' 'DARE' 'DAVIDSON' 'DAVIE' 'DUPLIN'
 'DURHAM' 'EDGECOMBE' 'GUILFORD' 'HALIFAX' 'HARNETT' 'HAYWOOD' 'HENDERSON'
 'HERTFORD' 'HYDE' 'JOHNSTON' 'JONES' 'LEE' 'LINCOLN' 'MARTIN'
 'MECKLENBURG' 'MOORE' 'NASH' 'NEW HANOVER' 'NORTHAMPTON' 'ORANGE'
 'PASQUOTANK' 'PITT' 'POLK' 'RICHMOND' 'SCOTLAND' 'STOKES' 'SURRY'
 'TYRRELL' 'WAKE' 'WASHINGTON' 'WATAUGA' 'WAYNE' 'WILKES' 'YADKIN']


In [8]:
halifax = sorted_concat[sorted_concat['County']=='HALIFAX']
halifax['Precinct'] = halifax['Precinct Name'].apply(lambda x: x.split('_')[0])
halifax['Contest Name'] = halifax['Contest Name'].apply(lambda x: x.split(' -')[0])
sorted_concat_drop_halifax = sorted_concat[sorted_concat['County']!='HALIFAX']
sorted_concat_halifax = pd.concat([halifax,sorted_concat_drop_halifax])
display(halifax)

<ipython-input-8-287a1d6944ae>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  halifax['Precinct'] = halifax['Precinct Name'].apply(lambda x: x.split('_')[0])
<ipython-input-8-287a1d6944ae>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  halifax['Contest Name'] = halifax['Contest Name'].apply(lambda x: x.split(' -')[0])


county_id   County Election Date result_type_lbl result_type_desc  \
0             42  HALIFAX    03/03/2020             STD         <NORMAL>   
1             42  HALIFAX    03/03/2020             STD         <NORMAL>   
2             42  HALIFAX    03/03/2020             STD         <NORMAL>   
3             42  HALIFAX    03/03/2020             STD         <NORMAL>   
4             42  HALIFAX    03/03/2020             STD         <NORMAL>   
...          ...      ...           ...             ...              ...   
23480         42  HALIFAX    03/03/2020             STD         <NORMAL>   
23481         42  HALIFAX    03/03/2020             STD         <NORMAL>   
23482         42  HALIFAX    03/03/2020             STD         <NORMAL>   
23483         42  HALIFAX    03/03/2020             STD         <NORMAL>   
23484         42  HALIFAX    03/03/2020             STD         <NORMAL>   

       contest_id             Contest Name Choice Party  contest_vote_for  \
0             116  PRESIDENTIAL PREFERENCE          CST                 1   
1             116  PRESIDENTIAL PREFERENCE          CST                 1   
2             116  PRESIDENTIAL PREFERENCE          CST                 1   
3             116  PRESIDENTIAL PREFERENCE          CST                 1   
4             116  PRESIDENTIAL PREFERENCE          CST                 1   
...           ...                      ...          ...               ...   
23480         127  PRESIDENTIAL PREFERENCE          GRE                 1   
23481         127  PRESIDENTIAL PREFERENCE          GRE                 1   
23482         127  PRESIDENTIAL PREFERENCE          GRE                 1   
23483         127  PRESIDENTIAL PREFERENCE          GRE                 1   
23484         127  PRESIDENTIAL PREFERENCE          GRE                 1   

      Precinct             Precinct Name  candidate_id           Choice  \
0        FAUCT             FAUCT_FAUCETT             1  Don Blankenship   
1        FAUCT             FAUCT_FAUCETT             1  Don Blankenship   
2        FAUCT             FAUCT_FAUCETT             1  Don Blankenship   
3          HAL               HAL_HALIFAX             1  Don Blankenship   
4          HAL               HAL_HALIFAX             1  Don Blankenship   
...        ...                       ...           ...              ...   
23480    RR1-2  RR1-2_ROANOKE RAPIDS 1-2             2    No Preference   
23481    RR1-2  RR1-2_ROANOKE RAPIDS 1-2             2    No Preference   
23482    RR1-2  RR1-2_ROANOKE RAPIDS 1-2             2    No Preference   
23483    RR1-2  RR1-2_ROANOKE RAPIDS 1-2             2    No Preference   
23484    RR1-2  RR1-2_ROANOKE RAPIDS 1-2             2    No Preference   

      Choice Party  group_num group_name voting_method voting method_rslt  \
0              CST          4        NaN             M               MAIL   
1              CST          5        NaN             P        PROVISIONAL   
2              CST          6        NaN             T           TRANSFER   
3              CST          2        NaN             V       ELECTION DAY   
4              CST          3        NaN             O           ONE STOP   
...            ...        ...        ...           ...                ...   
23480          GRE          2        NaN             V       ELECTION DAY   
23481          GRE          3        NaN             O           ONE STOP   
23482          GRE          4        NaN             M               MAIL   
23483          GRE          5        NaN             P        PROVISIONAL   
23484          GRE          6        NaN             T           TRANSFER   

       Total Votes  precinct_cd  
0                0          5.0  
1                0          5.0  
2                0          5.0  
3                0          6.0  
4                0          6.0  
...            ...          ...  
23480            0         12.0  
23481            0         12.0  
23482            0         12.0  
234

In [9]:
#Sum votes 
sorted_concat_mod = sorted_concat_halifax.groupby(['County', 'Contest Name', 'Precinct', 'Choice'])["Total Votes"].sum().reset_index()

In [10]:
print(sorted_concat_mod['County'].unique())
print(len(sorted_concat_mod['County'].unique()))

['ALLEGHANY' 'AVERY' 'BEAUFORT' 'BERTIE' 'BLADEN' 'BUNCOMBE' 'CABARRUS'
 'CALDWELL' 'CAMDEN' 'CURRITUCK' 'DARE' 'DAVIDSON' 'DAVIE' 'DUPLIN'
 'DURHAM' 'EDGECOMBE' 'GUILFORD' 'HALIFAX' 'HARNETT' 'HAYWOOD' 'HENDERSON'
 'HERTFORD' 'HYDE' 'JOHNSTON' 'JONES' 'LEE' 'LINCOLN' 'MARTIN'
 'MECKLENBURG' 'MOORE' 'NASH' 'NEW HANOVER' 'NORTHAMPTON' 'ORANGE'
 'PASQUOTANK' 'PITT' 'POLK' 'RICHMOND' 'SCOTLAND' 'STOKES' 'SURRY'
 'TYRRELL' 'WAKE' 'WASHINGTON' 'WATAUGA' 'WAYNE' 'WILKES' 'YADKIN']
48


In [11]:
#combine
election_results = pd.concat([unsorted_drop,sorted_concat_mod], axis=0, ignore_index=True)
print((election_results['County'].unique()))

['ROWAN' 'BRUNSWICK' 'COLUMBUS' 'CUMBERLAND' 'CARTERET' 'SAMPSON'
 'CATAWBA' 'WILSON' 'RUTHERFORD' 'GATES' 'LENOIR' 'MITCHELL' 'ONSLOW'
 'FORSYTH' 'CLEVELAND' 'CHEROKEE' 'ALEXANDER' 'UNION' 'PERSON' 'FRANKLIN'
 'ROBESON' 'MONTGOMERY' 'PERQUIMANS' 'IREDELL' 'CASWELL' 'CRAVEN'
 'JACKSON' 'GRANVILLE' 'CHOWAN' 'ALAMANCE' 'STANLY' 'MCDOWELL' 'BURKE'
 'ASHE' 'ANSON' 'MACON' 'PENDER' 'GASTON' 'HOKE' 'WARREN' 'GREENE'
 'PAMLICO' 'VANCE' 'YANCEY' 'TRANSYLVANIA' 'CLAY' 'CHATHAM' 'MADISON'
 'RANDOLPH' 'SWAIN' 'ROCKINGHAM' 'GRAHAM' 'ALLEGHANY' 'AVERY' 'BEAUFORT'
 'BERTIE' 'BLADEN' 'BUNCOMBE' 'CABARRUS' 'CALDWELL' 'CAMDEN' 'CURRITUCK'
 'DARE' 'DAVIDSON' 'DAVIE' 'DUPLIN' 'DURHAM' 'EDGECOMBE' 'GUILFORD'
 'HALIFAX' 'HARNETT' 'HAYWOOD' 'HENDERSON' 'HERTFORD' 'HYDE' 'JOHNSTON'
 'JONES' 'LEE' 'LINCOLN' 'MARTIN' 'MECKLENBURG' 'MOORE' 'NASH'
 'NEW HANOVER' 'NORTHAMPTON' 'ORANGE' 'PASQUOTANK' 'PITT' 'POLK'
 'RICHMOND' 'SCOTLAND' 'STOKES' 'SURRY' 'TYRRELL' 'WAKE' 'WASHINGTON'
 'WATAUGA' 'WAYNE' 'WILKES' 'YAD

### Subset by contests of interest

In [12]:
contest_list = sorted(election_results['Contest Name'].unique())
keep_contests = []
for i in contest_list:
    if i.startswith('US '):
        keep_contests.append(i)
    elif i.startswith('NC '):
        if i.startswith('NC DISTRICT'):
            continue
        elif str('JUDGE DISTRICT') in str(i):
            continue
        else:
            keep_contests.append(i)
    elif i.startswith('PRESIDENTIAL'):
        keep_contests.append(i)
    else:
        continue

In [13]:
#Subset, remove over/under counts and clean Write-In candidates
election_sub = election_results[election_results['Contest Name'].isin(keep_contests)]
election_sub = election_sub[~election_sub['Choice'].isin(['OVER VOTE','UNDER VOTE','OVER VOTES','UNDER VOTES'])]
election_sub['Choice'] = election_sub['Choice'].apply(lambda x: 'Write-In' if 'Write' in x else x)
election_sub['Choice'] = election_sub.apply(lambda x: '_'.join([x['Contest Name'],x['Choice']]) if x['Choice']=='No Preference' else x['Choice'],axis=1)

### Create party field

In [14]:
election_sub['PARTY'] = election_sub['Choice Party'].apply(lambda x: str(x)[0])
print(election_sub['PARTY'].value_counts())

n    180934
D     54816
R     45438
L     20966
C      3684
G      2456
Name: PARTY, dtype: int64


In [15]:
#Retrieve original party data from the unsorted and input it into the new dataframe
cand_party_dict = dict(zip(list(election_sub['Choice']),list(election_sub['PARTY'])))
for k,v in cand_party_dict.items():
    if v == 'n': #if the value is null
        df = unsorted[unsorted['Choice']==k]
        party_list = df['Choice Party'].unique()
        if len(party_list) == 1: #only one unique party
            party = party_list[0]
            #if party.startswith('U'): #this is the Independent designation in NC, for this project they will be considered the equivalent of write-ins
            #    party = 'O' #write in designation
            election_sub['PARTY'] = election_sub.apply(lambda x: party if x['Choice'] == k else x['PARTY'],axis=1)
            if str(party) == 'n':
                print('There is no party still for: ', k)
        elif len(party_list) == 0:
            party = 'N'
            election_sub['PARTY'] = election_sub.apply(lambda x: party if x['Choice'] == k else x['PARTY'],axis=1)
        else:
            print('For ', k, ' there are multiple parties. They are: ', party_list)
election_sub['PARTY'] = election_sub['PARTY'].apply(lambda x: str(x)[0])

print(election_sub['PARTY'].value_counts())

D    134392
R    110854
L     49732
C      7272
G      4250
N      1794
Name: PARTY, dtype: int64


### Assign legislative level field

In [16]:
election_sub['LEVEL'] = election_sub.apply(lambda x: 'PRE' if 'PRESIDENTIAL' in x['Contest Name'] else x['Contest Name'],axis=1)
election_sub['LEVEL'] = election_sub.apply(lambda x: 'AGR' if 'AGRICULT' in x['Contest Name'] else x['LEVEL'],axis=1)
election_sub['LEVEL'] = election_sub.apply(lambda x: 'AUD' if 'AUDITOR' in x['Contest Name'] else x['LEVEL'],axis=1)
election_sub['LEVEL'] = election_sub.apply(lambda x: 'LTG' if 'LIEUTENANT' in x['Contest Name'] else x['LEVEL'],axis=1)
election_sub['LEVEL'] = election_sub.apply(lambda x: 'SPI' if 'SUPERINTENDENT' in x['Contest Name'] else x['LEVEL'],axis=1)
election_sub['LEVEL'] = election_sub.apply(lambda x: 'USS' if 'US SENATE' in x['Contest Name'] else x['LEVEL'],axis=1)
election_sub['LEVEL'] = election_sub.apply(lambda x: 'INS' if 'INSURANCE' in x['Contest Name'] else x['LEVEL'],axis=1)
election_sub['LEVEL'] = election_sub.apply(lambda x: 'SL' if 'NC HOUSE' in x['Contest Name'] else x['LEVEL'],axis=1)
election_sub['LEVEL'] = election_sub.apply(lambda x: 'SU' if 'NC STATE SENATE' in x['Contest Name'] else x['LEVEL'],axis=1)
election_sub['LEVEL'] = election_sub.apply(lambda x: 'GOV' if 'GOVERNOR' in x['Contest Name'] else x['LEVEL'],axis=1)
election_sub['LEVEL'] = election_sub.apply(lambda x: 'LBR' if 'LABOR' in x['Contest Name'] else x['LEVEL'],axis=1)
election_sub['LEVEL'] = election_sub.apply(lambda x: 'ATG' if 'ATTORNEY' in x['Contest Name'] else x['LEVEL'],axis=1)
election_sub['LEVEL'] = election_sub.apply(lambda x: 'CON' if 'US HOUSE' in x['Contest Name'] else x['LEVEL'],axis=1)
election_sub['LEVEL'] = election_sub.apply(lambda x: 'TRE' if 'TREASURER' in x['Contest Name'] else x['LEVEL'],axis=1)
election_sub['LEVEL'] = election_sub.apply(lambda x: 'SOS' if 'SECRETARY' in x['Contest Name'] else x['LEVEL'],axis=1)
statewide_contests = ['PRE','AGR','AUD','LTG','SPI','USS','INS','GOV','LBR','ATG','TRE','SOS']
print(election_sub['LEVEL'].unique())
election_sub.head()

['PRE' 'AGR' 'AUD' 'GOV' 'SPI' 'USS' 'INS' 'SL' 'TRE' 'SOS' 'CON' 'ATG'
 'SU' 'LBR']


County Election Date  Precinct  Contest Group ID Contest Type  \
0       ROWAN    03/03/2020        24            2864.0            S   
1   BRUNSWICK    03/03/2020        06            1032.0            S   
2    COLUMBUS    03/03/2020       P03            1027.0            S   
3  CUMBERLAND    03/03/2020  ABSENTEE            2447.0            S   
4    CARTERET    03/03/2020      ATSL            2450.0            S   

                           Contest Name                    Choice  \
0         PRESIDENTIAL PREFERENCE (LIB)            Vermin Supreme   
1  NC COMMISSIONER OF AGRICULTURE (DEM)  Donovan Alexander Watson   
2                      NC AUDITOR (DEM)            Luis A. Toledo   
3          NC LIEUTENANT GOVERNOR (DEM)              Chaz Beasley   
4          NC LIEUTENANT GOVERNOR (REP)             Greg Gebhardt   

  Choice Party  Vote For  Election Day  One Stop  Absentee by Mail  \
0          LIB       1.0           0.0       0.0               0.0   
1          DEM       1.0           8.0      11.0               0.0   
2          DEM       1.0           8.0       0.0               0.0   
3          DEM       1.0           0.0       0.0              36.0   
4          REP       1.0           5.0       0.0               0.0   

   Provisional  Total Votes Real Precinct PARTY LEVEL  
0          0.0            0             Y     L   PRE  
1          3.0           22             Y     D   AGR  
2          0.0            8             Y     D   AUD  
3          0.0           36             N     D   GOV  
4          0.0            5             Y     R   GOV

### Create last name field with first three letters

In [17]:
election_sub['LASTNAME'] = election_sub['Choice'].apply(lambda x: x.split(' ')[-1])
election_sub['LASTNAME'] = election_sub.apply(lambda x: x['Choice'].split(' ')[-2] if x['LASTNAME'] in ['II','III','Jr.','Sr.'] else x['LASTNAME'],axis=1)
election_sub['LASTNAME'] = election_sub['LASTNAME'].apply(lambda x: x.replace(',',''))
election_sub['LASTNAME'] = election_sub['LASTNAME'].apply(lambda x: x.strip())
election_sub['RESTNAME'] = election_sub.apply(lambda x: x['Choice'].replace(x['LASTNAME'],''),axis=1)
election_sub['RESTNAME'] = election_sub['RESTNAME'].apply(lambda x: x.replace(' , ',' '))
election_sub['WHOLENAME'] = election_sub.apply(lambda x: ', '.join([x['LASTNAME'],x['RESTNAME']]),axis=1)
election_sub['WHOLENAME'] = election_sub['WHOLENAME'].apply(lambda x: 'No Preference' if x.startswith('Preference') else x)
party_dict = {'D':'(DEM)','R':'(REP)','L':'(LIB)','N':'','G':'(GRE)','C':'(CON)'}
election_sub['PARTY3'] = election_sub['PARTY'].apply(lambda x: party_dict.get(x))
election_sub['CONTEST'] = election_sub['Contest Name'].apply(lambda x: x.upper())
election_sub['NAME_PARTY'] = election_sub.apply(lambda x: ' '.join([x['WHOLENAME'],x['PARTY3']]),axis=1)
election_sub['FIELDS_VAL'] = election_sub.apply(lambda x: ', '.join([x['NAME_PARTY'],x['CONTEST']]),axis=1)
display(election_sub[election_sub['PARTY3']==''])
display(election_sub.head())
display(election_sub.tail())

County Election Date                Precinct  Contest Group ID  \
139379    ALLEGHANY           NaN                      01               NaN   
139419    ALLEGHANY           NaN                     03A               NaN   
139459    ALLEGHANY           NaN                      04               NaN   
139499    ALLEGHANY           NaN                     06A               NaN   
139539    ALLEGHANY           NaN                ABSENTEE               NaN   
139579    ALLEGHANY           NaN                ONE STOP               NaN   
139619    ALLEGHANY           NaN             PROVISIONAL               NaN   
141700        AVERY           NaN                      01               NaN   
141740        AVERY           NaN                      02               NaN   
141780        AVERY           NaN                      03               NaN   
141820        AVERY           NaN                      04               NaN   
141860        AVERY           NaN                      05               NaN   
141900        AVERY           NaN                      06               NaN   
141940        AVERY           NaN                      07               NaN   
141980        AVERY           NaN                      08               NaN   
142020        AVERY           NaN                      09               NaN   
142060        AVERY           NaN                      10               NaN   
142100        AVERY           NaN                      11               NaN   
142140        AVERY           NaN                      12               NaN   
142180        AVERY           NaN                      13               NaN   
142220        AVERY           NaN                      14               NaN   
142260        AVERY           NaN                      15               NaN   
142300        AVERY           NaN                      16               NaN   
142340        AVERY           NaN                      17               NaN   
142380        AVERY           NaN                      18               NaN   
142420        AVERY           NaN                      19               NaN   
142460        AVERY           NaN                ABSENTEE               NaN   
142500        AVERY           NaN                ONE STOP               NaN   
142540        AVERY           NaN             PROVISIONAL               NaN   
145216     BEAUFORT           NaN                ABSENTEE               NaN   
145256     BEAUFORT           NaN                   AUROR               NaN   
145296     BEAUFORT           NaN                   BEADM               NaN   
145336     BEAUFORT           NaN                   BELHV               NaN   
145376     BEAUFORT           NaN                    BLCK               NaN   
145416     BEAUFORT           NaN                   CHOCO               NaN   
145456     BEAUFORT           NaN                   EDWAR               NaN   
145496     BEAUFORT           NaN                   GILEA               NaN   
145536     BEAUFORT           NaN                      HB               NaN   
145576     BEAUFORT           NaN                    NCRK               NaN   
145616     BEAUFORT           NaN                    OLDF               NaN   
145656     BEAUFORT           NaN               OS AURORA               NaN   
145696     BEAUFORT           NaN             OS BELHAVEN               NaN   
145736     BEAUFORT           NaN                  OS BOE               NaN   
145776     BEAUFORT           NaN                   PANTE               NaN   
145816     BEAUFORT           NaN                   PINET               NaN   
145856     BEAUFORT           NaN             PROVISIONAL               NaN   
145896     BEAUFORT           NaN                   PSJW3               NaN   
145936     BEAUFORT           NaN                    RVRD               NaN   
145976     BEAUFORT           NaN                   SURBA               NaN   
146016     BEAUFORT           NaN                    TCRK      

County Election Date  Precinct  Contest Group ID Contest Type  \
0       ROWAN    03/03/2020        24            2864.0            S   
1   BRUNSWICK    03/03/2020        06            1032.0            S   
2    COLUMBUS    03/03/2020       P03            1027.0            S   
3  CUMBERLAND    03/03/2020  ABSENTEE            2447.0            S   
4    CARTERET    03/03/2020      ATSL            2450.0            S   

                           Contest Name                    Choice  \
0         PRESIDENTIAL PREFERENCE (LIB)            Vermin Supreme   
1  NC COMMISSIONER OF AGRICULTURE (DEM)  Donovan Alexander Watson   
2                      NC AUDITOR (DEM)            Luis A. Toledo   
3          NC LIEUTENANT GOVERNOR (DEM)              Chaz Beasley   
4          NC LIEUTENANT GOVERNOR (REP)             Greg Gebhardt   

  Choice Party  Vote For  Election Day  One Stop  Absentee by Mail  \
0          LIB       1.0           0.0       0.0               0.0   
1          DEM       1.0           8.0      11.0               0.0   
2          DEM       1.0           8.0       0.0               0.0   
3          DEM       1.0           0.0       0.0              36.0   
4          REP       1.0           5.0       0.0               0.0   

   Provisional  Total Votes Real Precinct PARTY LEVEL  LASTNAME  \
0          0.0            0             Y     L   PRE   Supreme   
1          3.0           22             Y     D   AGR    Watson   
2          0.0            8             Y     D   AUD    Toledo   
3          0.0           36             N     D   GOV   Beasley   
4          0.0            5             Y     R   GOV  Gebhardt   

             RESTNAME                   WHOLENAME PARTY3  \
0             Vermin             Supreme, Vermin   (LIB)   
1  Donovan Alexander   Watson, Donovan Alexander   (DEM)   
2            Luis A.             Toledo, Luis A.   (DEM)   
3               Chaz               Beasley, Chaz   (DEM)   
4               Greg              Gebhardt, Greg   (REP)   

                                CONTEST                        NAME_PARTY  \
0         PRESIDENTIAL PREFERENCE (LIB)            Supreme, Vermin  (LIB)   
1  NC COMMISSIONER OF AGRICULTURE (DEM)  Watson, Donovan Alexander  (DEM)   
2                      NC AUDITOR (DEM)            Toledo, Luis A.  (DEM)   
3          NC LIEUTENANT GOVERNOR (DEM)              Beasley, Chaz  (DEM)   
4          NC LIEUTENANT GOVERNOR (REP)             Gebhardt, Greg  (REP)   

                                          FIELDS_VAL  
0  Supreme, Vermin  (LIB), PRESIDENTIAL PREFERENC...  
1  Watson, Donovan Alexander  (DEM), NC COMMISSIO...  
2           Toledo, Luis A.  (DEM), NC AUDITOR (DEM)  
3  Beasley, Chaz  (DEM), NC LIEUTENANT GOVERNOR (...  
4  Gebhardt, Greg  (REP), NC LIEUTENANT GOVERNOR ...

County Election Date Precinct  Contest Group ID Contest Type  \
396276  YADKIN           NaN     SLIB               NaN          NaN   
396277  YADKIN           NaN     SLIB               NaN          NaN   
396278  YADKIN           NaN     SLIB               NaN          NaN   
396279  YADKIN           NaN     SLIB               NaN          NaN   
396280  YADKIN           NaN     SLIB               NaN          NaN   

       Contest Name            Choice Choice Party  Vote For  Election Day  \
396276    US SENATE       Paul Wright          NaN       NaN           NaN   
396277    US SENATE  Sharon Y. Hudson          NaN       NaN           NaN   
396278    US SENATE     Steve Swenson          NaN       NaN           NaN   
396279    US SENATE       Thom Tillis          NaN       NaN           NaN   
396280    US SENATE  Trevor M. Fuller          NaN       NaN           NaN   

        One Stop  Absentee by Mail  Provisional  Total Votes Real Precinct  \
396276       NaN               NaN          NaN           47           NaN   
396277       NaN               NaN          NaN           40           NaN   
396278       NaN               NaN          NaN            5           NaN   
396279       NaN               NaN          NaN          478           NaN   
396280       NaN               NaN          NaN            4           NaN   

       PARTY LEVEL LASTNAME    RESTNAME           WHOLENAME PARTY3    CONTEST  \
396276     R   USS   Wright       Paul        Wright, Paul   (REP)  US SENATE   
396277     R   USS   Hudson  Sharon Y.   Hudson, Sharon Y.   (REP)  US SENATE   
396278     D   USS  Swenson      Steve      Swenson, Steve   (DEM)  US SENATE   
396279     R   USS   Tillis       Thom        Tillis, Thom   (REP)  US SENATE   
396280     D   USS   Fuller  Trevor M.   Fuller, Trevor M.   (DEM)  US SENATE   

                      NAME_PARTY                           FIELDS_VAL  
396276       Wright, Paul  (REP)       Wright, Paul  (REP), US SENATE  
396277  Hudson, Sharon Y.  (REP)  Hudson, Sharon Y.  (REP), US SENATE  
396278     Swenson, Steve  (DEM)     Swenson, Steve  (DEM), US SENATE  
396279       Tillis, Thom  (REP)       Tillis, Thom  (REP), US SENATE  
396280  Fuller, Trevor M.  (DEM)  Fuller, Trevor M.  (DEM), US SENATE

In [18]:
election_sub['LNAME'] = election_sub['Choice'].apply(lambda x: x.split(' ')[-1])
election_sub['LNAME'] = election_sub['LNAME'].apply(lambda x: 'NPR' if str(x)=='Preference' else x)
#remove II, III, Jr., Sr.
election_sub['LNAME'] = election_sub.apply(lambda x: x['Choice'].split(' ')[-2] if x['LNAME'] in ['II','III','Jr.','Sr.'] else x['LNAME'],axis=1)
election_sub['LNAME'] = election_sub['LNAME'].apply(lambda x: x.replace("'",""))
#capitalize
election_sub['LNAME'] = election_sub['LNAME'].apply(lambda x: str(x[:3]).upper())

### Add district assignment field

In [19]:
election_sub['DIST'] = election_sub['Contest Name'].apply(lambda x: x.split(' ')[-1])
display(election_sub[election_sub['DIST']==''])
election_sub['DIST'] = election_sub.apply(lambda x: x['Contest Name'].split(' ')[-2] if len(x['DIST'])>3 else x['DIST'],axis=1)
display(election_sub[election_sub['DIST']==''])
election_sub['DIST'] = election_sub.apply(lambda x: 'STATEWIDE' if x['LEVEL'] in statewide_contests else x['DIST'], axis=1)
display(election_sub[election_sub['DIST']==''])
print(sorted(election_sub['DIST'].unique()))
display(election_sub)

Empty DataFrame
Columns: [County, Election Date, Precinct, Contest Group ID, Contest Type, Contest Name, Choice, Choice Party, Vote For, Election Day, One Stop, Absentee by Mail, Provisional, Total Votes, Real Precinct, PARTY, LEVEL, LASTNAME, RESTNAME, WHOLENAME, PARTY3, CONTEST, NAME_PARTY, FIELDS_VAL, LNAME, DIST]
Index: []

Empty DataFrame
Columns: [County, Election Date, Precinct, Contest Group ID, Contest Type, Contest Name, Choice, Choice Party, Vote For, Election Day, One Stop, Absentee by Mail, Provisional, Total Votes, Real Precinct, PARTY, LEVEL, LASTNAME, RESTNAME, WHOLENAME, PARTY3, CONTEST, NAME_PARTY, FIELDS_VAL, LNAME, DIST]
Index: []

Empty DataFrame
Columns: [County, Election Date, Precinct, Contest Group ID, Contest Type, Contest Name, Choice, Choice Party, Vote For, Election Day, One Stop, Absentee by Mail, Provisional, Total Votes, Real Precinct, PARTY, LEVEL, LASTNAME, RESTNAME, WHOLENAME, PARTY3, CONTEST, NAME_PARTY, FIELDS_VAL, LNAME, DIST]
Index: []

['003', '005', '006', '009', '01', '012', '014', '015', '019', '02', '020', '021', '022', '024', '025', '026', '027', '033', '035', '036', '037', '038', '04', '043', '044', '045', '05', '052', '053', '056', '059', '06', '060', '064', '066', '07', '071', '072', '075', '08', '080', '082', '083', '09', '093', '1', '10', '102', '11', '117', '119', '12', '18', '20', '27', '29', '33', '38', '42', '48', '49', '50', 'STATEWIDE']


County Election Date  Precinct  Contest Group ID Contest Type  \
0            ROWAN    03/03/2020        24            2864.0            S   
1        BRUNSWICK    03/03/2020        06            1032.0            S   
2         COLUMBUS    03/03/2020       P03            1027.0            S   
3       CUMBERLAND    03/03/2020  ABSENTEE            2447.0            S   
4         CARTERET    03/03/2020      ATSL            2450.0            S   
...            ...           ...       ...               ...          ...   
396276      YADKIN           NaN      SLIB               NaN          NaN   
396277      YADKIN           NaN      SLIB               NaN          NaN   
396278      YADKIN           NaN      SLIB               NaN          NaN   
396279      YADKIN           NaN      SLIB               NaN          NaN   
396280      YADKIN           NaN      SLIB               NaN          NaN   

                                Contest Name                    Choice  \
0              PRESIDENTIAL PREFERENCE (LIB)            Vermin Supreme   
1       NC COMMISSIONER OF AGRICULTURE (DEM)  Donovan Alexander Watson   
2                           NC AUDITOR (DEM)            Luis A. Toledo   
3               NC LIEUTENANT GOVERNOR (DEM)              Chaz Beasley   
4               NC LIEUTENANT GOVERNOR (REP)             Greg Gebhardt   
...                                      ...                       ...   
396276                             US SENATE               Paul Wright   
396277                             US SENATE          Sharon Y. Hudson   
396278                             US SENATE             Steve Swenson   
396279                             US SENATE               Thom Tillis   
396280                             US SENATE          Trevor M. Fuller   

       Choice Party  Vote For  Election Day  One Stop  Absentee by Mail  \
0               LIB       1.0           0.0       0.0               0.0   
1               DEM       1.0           8.0      11.0               0.0   
2               DEM       1.0           8.0       0.0               0.0   
3               DEM       1.0           0.0       0.0              36.0   
4               REP       1.0           5.0       0.0               0.0   
...             ...       ...           ...       ...               ...   
396276          NaN       NaN           NaN       NaN               NaN   
396277          NaN       NaN           NaN       NaN               NaN   
396278          NaN       NaN           NaN       NaN               NaN   
396279          NaN       NaN           NaN       NaN               NaN   
396280          NaN       NaN           NaN       NaN               NaN   

        Provisional  Total Votes Real Precinct PARTY LEVEL  LASTNAME  \
0               0.0            0             Y     L   PRE   Supreme   
1               3.0           22             Y     D   AGR    Watson   
2               0.0            8             Y     D   AUD    Toledo   
3               0.0           36             N     D   GOV   Beasley   
4               0.0            5             Y     R   GOV  Gebhardt   
...             ...          ...           ...   ...   ...       ...   
396276          NaN           47           NaN     R   USS    Wright   
396277          NaN           40           NaN     R   USS    Hudson   
396278          NaN            5           NaN     D   USS   Swenson   
396279          NaN          478           NaN     R   USS    Tillis   
396280          NaN            4           NaN     D   USS    Fuller   

                  RESTNAME                   WHOLENAME PARTY3  \
0                  Vermin             Supreme, Vermin   (LIB)   
1       Donovan Alexander   Watson, Donovan Alexander   (DEM)   
2                 Luis A.             Toledo, Luis A.   (DEM)   
3                    Chaz               Beasley, Chaz   (DEM)   
4                    Greg              Gebhardt, Greg   (REP)   
...                    ...                

In [20]:
election_sub['DIST'] = election_sub.apply(lambda x: x['DIST'].zfill(3) if x['LEVEL']=='SL' else x['DIST'].zfill(2),axis=1)
print(sorted(election_sub['DIST'].unique()))

['003', '005', '006', '009', '01', '012', '014', '015', '019', '02', '020', '021', '022', '024', '025', '026', '027', '033', '035', '036', '037', '038', '04', '043', '044', '045', '05', '052', '053', '056', '059', '06', '060', '064', '066', '07', '071', '072', '075', '08', '080', '082', '083', '09', '093', '10', '102', '11', '117', '119', '12', '18', '20', '29', '33', '38', '42', '48', '49', '50', 'STATEWIDE']


## Pivot the data

### Create pivot column and unique precinct ID

In [21]:
election_sub['PIVOT_COL'] = election_sub.apply(lambda x: ''.join(['P20',x['LEVEL'],x['PARTY'],x['LNAME']]) if x['DIST']=='STATEWIDE' else 'HOLD',axis=1)
election_sub['PIVOT_COL'] = election_sub.apply(lambda x: ''.join(['P',x['LEVEL'],x['DIST'],x['PARTY'],x['LNAME']]) if x['DIST']!='STATEWIDE' else x['PIVOT_COL'],axis=1)
fields_dict = dict(zip(list(election_sub['PIVOT_COL']),list(election_sub['FIELDS_VAL'])))
election_sub['prec_field'] = election_sub.apply(lambda x: '_'.join([x['Precinct'],x['County']]),axis=1)
election_sub.head()

County Election Date  Precinct  Contest Group ID Contest Type  \
0       ROWAN    03/03/2020        24            2864.0            S   
1   BRUNSWICK    03/03/2020        06            1032.0            S   
2    COLUMBUS    03/03/2020       P03            1027.0            S   
3  CUMBERLAND    03/03/2020  ABSENTEE            2447.0            S   
4    CARTERET    03/03/2020      ATSL            2450.0            S   

                           Contest Name                    Choice  \
0         PRESIDENTIAL PREFERENCE (LIB)            Vermin Supreme   
1  NC COMMISSIONER OF AGRICULTURE (DEM)  Donovan Alexander Watson   
2                      NC AUDITOR (DEM)            Luis A. Toledo   
3          NC LIEUTENANT GOVERNOR (DEM)              Chaz Beasley   
4          NC LIEUTENANT GOVERNOR (REP)             Greg Gebhardt   

  Choice Party  Vote For  Election Day  One Stop  Absentee by Mail  \
0          LIB       1.0           0.0       0.0               0.0   
1          DEM       1.0           8.0      11.0               0.0   
2          DEM       1.0           8.0       0.0               0.0   
3          DEM       1.0           0.0       0.0              36.0   
4          REP       1.0           5.0       0.0               0.0   

   Provisional  Total Votes Real Precinct PARTY LEVEL  LASTNAME  \
0          0.0            0             Y     L   PRE   Supreme   
1          3.0           22             Y     D   AGR    Watson   
2          0.0            8             Y     D   AUD    Toledo   
3          0.0           36             N     D   GOV   Beasley   
4          0.0            5             Y     R   GOV  Gebhardt   

             RESTNAME                   WHOLENAME PARTY3  \
0             Vermin             Supreme, Vermin   (LIB)   
1  Donovan Alexander   Watson, Donovan Alexander   (DEM)   
2            Luis A.             Toledo, Luis A.   (DEM)   
3               Chaz               Beasley, Chaz   (DEM)   
4               Greg              Gebhardt, Greg   (REP)   

                                CONTEST                        NAME_PARTY  \
0         PRESIDENTIAL PREFERENCE (LIB)            Supreme, Vermin  (LIB)   
1  NC COMMISSIONER OF AGRICULTURE (DEM)  Watson, Donovan Alexander  (DEM)   
2                      NC AUDITOR (DEM)            Toledo, Luis A.  (DEM)   
3          NC LIEUTENANT GOVERNOR (DEM)              Beasley, Chaz  (DEM)   
4          NC LIEUTENANT GOVERNOR (REP)             Gebhardt, Greg  (REP)   

                                          FIELDS_VAL LNAME       DIST  \
0  Supreme, Vermin  (LIB), PRESIDENTIAL PREFERENC...   SUP  STATEWIDE   
1  Watson, Donovan Alexander  (DEM), NC COMMISSIO...   WAT  STATEWIDE   
2           Toledo, Luis A.  (DEM), NC AUDITOR (DEM)   TOL  STATEWIDE   
3  Beasley, Chaz  (DEM), NC LIEUTENANT GOVERNOR (...   BEA  STATEWIDE   
4  Gebhardt, Greg  (REP), NC LIEUTENANT GOVERNOR ...   GEB  STATEWIDE   

    PIVOT_COL           prec_field  
0  P20PRELSUP             24_ROWAN  
1  P20AGRDWAT         06_BRUNSWICK  
2  P20AUDDTOL         P03_COLUMBUS  
3  P20GOVDBEA  ABSENTEE_CUMBERLAND  
4  P20GOVRGEB        ATSL_CARTERET

In [22]:
print(len(election_sub['County'].unique()))

100


### Pivot

In [23]:
pivoted_election_results = pd.pivot_table(election_sub,values=["Total Votes"],index=["prec_field"],columns=["PIVOT_COL"],aggfunc=sum)
pivoted_election_results.head()

Total Votes                                              \
PIVOT_COL    P20AGRDSMI P20AGRDWAD P20AGRDWAT P20ATGRHAY P20ATGRMUM   
prec_field                                                            
0001_BURKE        135.0      159.0       27.0      126.0      109.0   
0003_BURKE         28.0       33.0       14.0       67.0       52.0   
0003_STANLY        58.0       86.0       26.0       46.0       52.0   
0007_STANLY        62.0       66.0       20.0       50.0       55.0   
0008_STANLY        75.0       64.0       72.0        6.0        5.0   

                                                                               \
PIVOT_COL   P20ATGRONE P20AUDDTOL P20AUDDWOO P20AUDRHOE P20AUDRSTR P20GOVDBEA   
prec_field                                                                      
0001_BURKE       142.0       50.0      269.0      103.0      247.0       62.0   
0003_BURKE        74.0        9.0       64.0       44.0      143.0       15.0   
0003_STANLY      101.0       33.0      137.0       58.0      123.0       17.0   
0007_STANLY       88.0       23.0      132.0       54.0      122.0       16.0   
0008_STANLY        9.0       52.0      156.0        2.0       17.0       29.0   

                                                                               \
PIVOT_COL   P20GOVDCOO P20GOVDDUY P20GOVDHOL P20GOVDNEW P20GOVDREE P20GOVDTHO   
prec_field                                                                      
0001_BURKE       306.0       52.0       83.0       47.0       48.0       49.0   
0003_BURKE        71.0        5.0       15.0        9.0       15.0       17.0   
0003_STANLY      170.0       34.0       39.0       15.0       32.0       39.0   
0007_STANLY      137.0       16.0       49.0       23.0       32.0       32.0   
0008_STANLY      184.0        7.0       59.0       17.0       56.0       79.0   

                                                                               \
PIVOT_COL   P20GOVDTOO P20GOVRBEN P20GOVRCOC P20GOVRELL P20GOVRFOR P20GOVRGEB   
prec_field                                                                      
0001_BURKE        24.0        7.0       21.0        6.0      373.0       11.0   
0003_BURKE        12.0        1.0       10.0        5.0      186.0        1.0   
0003_STANLY       25.0        4.0       18.0        7.0      193.0       12.0   
0007_STANLY       17.0        4.0       10.0        2.0      191.0       12.0   
0008_STANLY       17.0        0.0        1.0        0.0       16.0        2.0   

                                                                               \
PIVOT_COL   P20GOVRGRA P20GOVRJOH P20GOVRRIT P20GOVRROB P20GOVRSTO P20GOVRWEL   
prec_field                                                                      
0001_BURKE        33.0       43.0       46.0      158.0       25.0       68.0   
0003_BURKE        16.0       19.0       19.0       89.0       16.0       32.0   
0003_STANLY       31.0       25.0       43.0       57.0       11.0       24.0   
0007_STANLY       21.0       23.0       35.0       63.0       24.0       25.0   
0008_STANLY        3.0        1.0        2.0       12.0        1.0        0.0   

                                                                               \
PIVOT_COL   P20INSRCAU P20INSRPIE P20LBRRDOB P20LBRRFLO P20LBRRSTA P20PRECBLA   
prec_field                                                                      
0001_BURKE       207.0      149.0      144.0       56.0      156.0        0.0   
0003_BURKE       105.0       80.0       79.0       41.0       67.0        0.0   
0003_STANLY      121.0       71.0       59.0       44.0       78.0        0.0   
0007_STANLY      125.0       57.0       88.0       26.0       69.0        0.0   
0008_STANLY        7.0       12.0       10.0        2.0        5.0        0.0   

                                                                               \
PIVOT_COL   P20PRECKRA P20PRECNPR P20PREDBEN P20PREDBID P20PREDBLO P20PREDBOO   
prec_field                          

### Clean the pivoted data

In [24]:
#Fill in N/A with 0
pivoted_election_results = pivoted_election_results.fillna(0)

#Clean the columns
pivoted_election_results.reset_index(drop=False,inplace=True)
pivoted_election_results.columns = pivoted_election_results.columns.droplevel(0)
pivoted_election_results.rename(columns={pivoted_election_results.columns[0]: 'PREC_CO'},inplace=True)
pivoted_election_results['PRECINCT'] = pivoted_election_results['PREC_CO'].apply(lambda x: x.split('_')[0])
pivoted_election_results['COUNTY'] = pivoted_election_results['PREC_CO'].apply(lambda x: x.split('_')[1])
pivoted_election_results.head()

PIVOT_COL      PREC_CO  P20AGRDSMI  P20AGRDWAD  P20AGRDWAT  P20ATGRHAY  \
0           0001_BURKE       135.0       159.0        27.0       126.0   
1           0003_BURKE        28.0        33.0        14.0        67.0   
2          0003_STANLY        58.0        86.0        26.0        46.0   
3          0007_STANLY        62.0        66.0        20.0        50.0   
4          0008_STANLY        75.0        64.0        72.0         6.0   

PIVOT_COL  P20ATGRMUM  P20ATGRONE  P20AUDDTOL  P20AUDDWOO  P20AUDRHOE  \
0               109.0       142.0        50.0       269.0       103.0   
1                52.0        74.0         9.0        64.0        44.0   
2                52.0       101.0        33.0       137.0        58.0   
3                55.0        88.0        23.0       132.0        54.0   
4                 5.0         9.0        52.0       156.0         2.0   

PIVOT_COL  P20AUDRSTR  P20GOVDBEA  P20GOVDCOO  P20GOVDDUY  P20GOVDHOL  \
0               247.0        62.0       306.0        52.0        83.0   
1               143.0        15.0        71.0         5.0        15.0   
2               123.0        17.0       170.0        34.0        39.0   
3               122.0        16.0       137.0        16.0        49.0   
4                17.0        29.0       184.0         7.0        59.0   

PIVOT_COL  P20GOVDNEW  P20GOVDREE  P20GOVDTHO  P20GOVDTOO  P20GOVRBEN  \
0                47.0        48.0        49.0        24.0         7.0   
1                 9.0        15.0        17.0        12.0         1.0   
2                15.0        32.0        39.0        25.0         4.0   
3                23.0        32.0        32.0        17.0         4.0   
4                17.0        56.0        79.0        17.0         0.0   

PIVOT_COL  P20GOVRCOC  P20GOVRELL  P20GOVRFOR  P20GOVRGEB  P20GOVRGRA  \
0                21.0         6.0       373.0        11.0        33.0   
1                10.0         5.0       186.0         1.0        16.0   
2                18.0         7.0       193.0        12.0        31.0   
3                10.0         2.0       191.0        12.0        21.0   
4                 1.0         0.0        16.0         2.0         3.0   

PIVOT_COL  P20GOVRJOH  P20GOVRRIT  P20GOVRROB  P20GOVRSTO  P20GOVRWEL  \
0                43.0        46.0       158.0        25.0        68.0   
1                19.0        19.0        89.0        16.0        32.0   
2                25.0        43.0        57.0        11.0        24.0   
3                23.0        35.0        63.0        24.0        25.0   
4                 1.0         2.0        12.0         1.0         0.0   

PIVOT_COL  P20INSRCAU  P20INSRPIE  P20LBRRDOB  P20LBRRFLO  P20LBRRSTA  \
0               207.0       149.0       144.0        56.0       156.0   
1               105.0        80.0        79.0        41.0        67.0   
2               121.0        71.0        59.0        44.0        78.0   
3               125.0        57.0        88.0        26.0        69.0   
4                 7.0        12.0        10.0         2.0         5.0   

PIVOT_COL  P20PRECBLA  P20PRECKRA  P20PRECNPR  P20PREDBEN  P20PREDBID  \
0                 0.0         0.0         0.0         2.0       173.0   
1                 0.0         0.0         0.0         0.0        38.0   
2                 0.0         0.0         0.0         0.0       115.0   
3                 0.0         0.0         0.0         0.0       120.0   
4                 0.0         0.0         0.0         2.0       171.0   

PIVOT_COL  P20PREDBLO  P20PREDBOO  P20PREDBUT  P20PREDCAS  P20PREDDEL  \
0                44.0         1.0         8.0         0.0         2.0   
1                13.0         1.0         4.0         0.0         1.0   
2                30.0         0.0         1.0         0.0         0.0   
3                14.0         0.0         0.0         0.0         0.0   
4                19.0         0.0         2.0         1.0         0.0   

PIVOT_COL  P20PREDGAB  P20PREDKLO  P20PREDN

In [25]:
print(len(pivoted_election_results['COUNTY'].unique()))

100


## Allocate absentee votes

In [26]:
def allocate_absentee(df_receiving_votes,df_allocating,column_list,col_allocating):
    original_cols = list(df_receiving_votes.columns)
    
    #Add in the "Total Votes column"
    df_receiving_votes.loc[:,"Total_Votes"]=0
    for race in column_list:
        df_receiving_votes.loc[:,"Total_Votes"]+=df_receiving_votes.loc[:,race]
    
    #Create the needed dataframes
    precinct_specific_totals = pd.DataFrame(df_receiving_votes.groupby([col_allocating]).sum())
    precinct_specific_totals.reset_index(drop=False,inplace=True)
    to_dole_out_totals = pd.DataFrame(df_allocating.groupby([col_allocating]).sum())
    to_dole_out_totals.reset_index(drop=False,inplace=True)
    
    #Print out any instances where the allocation, as written, won't work
    special_allocation_needed = []
    for index, row in precinct_specific_totals.iterrows():
        for race in column_list:
            if (row[race]==0):
                race_district = row[col_allocating]
                if race_district in to_dole_out_totals[col_allocating].unique():
                    to_allocate = int(to_dole_out_totals.loc[to_dole_out_totals[col_allocating]==race_district][race])
                    if (to_allocate != 0):
                        special_allocation_needed.append([race_district,race])
    
    #Create some new columns for each of these races to deal with the allocation
    for race in column_list:
        add_var = race+"_add"
        rem_var = race+"_rem"
        floor_var = race+"_floor"
        df_receiving_votes.loc[:,add_var]=0.0
        df_receiving_votes.loc[:,rem_var]=0.0
        df_receiving_votes.loc[:,floor_var]=0.0

    #Iterate over the rows
    #Note this function iterates over the dataframe two times so the rounded vote totals match the totals to allocate
    for index, row in df_receiving_votes.iterrows():
        if row[col_allocating] in to_dole_out_totals[col_allocating].unique():
            for race in column_list:
                add_var = race+"_add"
                rem_var = race+"_rem"
                floor_var = race+"_floor"
                #Grab the district
                county_id = row[col_allocating]
                if [county_id,race] in special_allocation_needed:
                    #Get the denominator for the allocation - the summed "total votes" for precincts in that grouping
                    denom = precinct_specific_totals.loc[precinct_specific_totals[col_allocating]==county_id]["Total_Votes"]
                    #Get one of the numerators, how many districtwide votes to allocate
                    numer = to_dole_out_totals.loc[to_dole_out_totals[col_allocating]==county_id][race]
                    #Get the "total votes" for this particular precinct
                    val = df_receiving_votes.at[index,"Total_Votes"]
                    #Get the vote share, the precincts % of total precinct votes in the district times votes to allocate
                else:
                    #Get the denominator for the allocation (the precinct vote totals)
                    denom = precinct_specific_totals.loc[precinct_specific_totals[col_allocating]==county_id][race]
                    #Get one of the numerators, how many districtwide votes to allocate
                    numer = to_dole_out_totals.loc[to_dole_out_totals[col_allocating]==county_id][race]
                    #Get the vote totals for this race in this precinct
                    val = df_receiving_votes.at[index,race]
                    #Get the vote share, the precincts % of total precinct votes in the district times votes to allocate
                if ((float(denom)==0)):
                    vote_share = 0
                else:
                    vote_share = (float(val)/float(denom))*float(numer)
                df_receiving_votes.at[index,add_var] = vote_share
                #Take the decimal remainder of the allocation
                df_receiving_votes.at[index,rem_var] = vote_share%1
                #Take the floor of the allocation
                df_receiving_votes.at[index,floor_var] = np.floor(vote_share)

    #After the first pass through, get the sums of the races by district to assist in the rounding            
    first_allocation = pd.DataFrame(df_receiving_votes.groupby([col_allocating]).sum())

    #Now we want to iterate district by district to work on rounding
    county_list = list(to_dole_out_totals[col_allocating].unique()) 

    #Iterate over the district
    for county in county_list:
        for race in column_list:
            add_var = race+"_add"
            rem_var = race+"_rem"
            floor_var = race+"_floor"
            #County how many votes still need to be allocated (because we took the floor of all the initial allocations)
            to_go = int(np.round((int(to_dole_out_totals.loc[to_dole_out_totals[col_allocating]==county][race])-first_allocation.loc[first_allocation.index==county,floor_var])))
            #Grab the n precincts with the highest remainders and round these up, where n is the # of votes that still need to be allocated
            for index in df_receiving_votes.loc[df_receiving_votes[col_allocating]==county][rem_var].nlargest(to_go).index:
                df_receiving_votes.at[index,add_var] = np.ceil(df_receiving_votes.at[index,add_var])

    #Iterate over every race again
    for race in column_list:
        add_var = race+"_add"
        #Round every allocation down to not add fractional votes
        df_receiving_votes.loc[:,add_var]=np.floor(df_receiving_votes.loc[:,add_var])
        df_receiving_votes.loc[:,race]+=df_receiving_votes.loc[:,add_var]
        
    df_receiving_votes = df_receiving_votes[original_cols]
    
    return df_receiving_votes

### Create dataframe of votes to allocate

In [27]:
#List of non-physical precincts to remove for dataframe to allocate
searchfor = ['ABSENTEE', 'ONE STOP', 'ONE STOP ARB', 'ONE STOP BOE', 'ONE STOP CBC', 'ONE STOP CFC', 'ONE STOP CFN', 'ONE STOP GVT', 'ONE STOP HOS', 'ONE STOP MSL', 'ONE STOP NLB', 'ONE STOP PVL', 'ONE STOP SRC', 'PROVISIONAL', 'TRANSFER']
searchfor = searchfor+['OS AG CENTER','OS CJRC','OS COMM SCHOOLS','OS DUKE','OS ENO','OS EPPES','OS ERL','OS FARMVILLE','OS GETG','OS HVBC','OS ML','OS MSUMC','OS NCCU','OS NRL','OS SHS','OS SRL','OS STUDENT CENTER','OS TRC','OS WILLIS BUILDING','OS WINTERVILLE','ABSENTEE MAIL','ABSENTEE BY MAIL','ABSENTEE SUPPLEMENTAL','AVML','AVOM','AURORA OS','ARCHER LODGE','ELK OS','LINCOLN OS','BOE OS','BOE OFFICE','BMBL','PM OS']
searchfor = searchfor+['HACC', 'OS GASTON', 'BOOK T. WASHINGTON', 'OS TLIB', 'EAST ARCADIA', 'ONE STOP AG', 'MURFREE CNTR', 'OSCA 1-40', 'OS LITTLETON', 'ONE STOP VTH', 'OSKD 121-128', 'OSLL 1-40', 'OSWO 1-40', 'LSKY', 'OSAP 81-120', 'OS BOE', 'OSAP 41-80', 'OS RINGWOOD', 'OSWO 81-120', 'OS WARSAW', 'PROVI 1-40', 'CHOCO OS', 'BAY TREE FIRE DEPT', 'OS WW', 'OS LOB', 'OSAP 121-128', 'OSOP 81-120', 'OSBR 121-128', 'OS PHL', 'ONE STOP THREE', 'OSKD 41-80', 'OSBR 81-120', 'OS CARRBORO', 'FVCC', 'OSAB 121-128', 'OSRB 1-40', 'OSTA 1-40', 'ONE STOP ANNEX CONF RM', 'OS OCK', 'OSAV 121-128', 'OSLH 1-40', 'ONE STOP RS', 'SBBL', 'OS HALES', 'OSLH 41-80', 'BLAD COUNTY GYM', 'REYV', 'OS UM', 'OSWO 41-80', 'RMT 301 OS', 'OS MAX', 'OSAV 81-120', 'NASHVILLE OS', 'OSGR 81-120', 'CLEVELAND', 'CLAYTON', 'OSTA 121-128', 'WEST OS', 'OS ETOWAH', 'ONE STOP TWO', 'OSOP 1-40', 'ONE STOP KING', 'OSNR 41-80', 'OSRB 81-120', 'PROVI 121-128', 'OS RICHSQUARE', 'SPAULDING MONROE', 'OSCS 81-120', 'CO OP', 'OSOP 41-80', 'RMT DOWNTOWN OS', 'OS MOT', 'OSWN 81-120', 'OSZB 41-80', 'OSWN 41-80', 'OSNR 1-40', 'OS FLAT ROCK', 'OSLL 121-128', 'OS SEVERN', 'OS RESOURCE CENTER', 'MT. PLEASANT OS', 'OSAV 41-80', 'SELMA', 'TRANS 1-40', 'OS SEYMOUR', 'OS HAR', 'OS MCSWAIN', 'OSZB 81-120', 'ONE-STOP', 'UNCA', 'OSNR 121-128', 'OS CAE', 'OS MIDWAY FIRE DEPT', 'OS SCOTLAND NECK', 'OSCM 41-80', 'OS EFLAND', 'DET OF SOCIAL SERVICES', 'OSCA 121-128', 'OSWA 41-80', 'OSRB 41-80', 'BTFD', 'OSHS 1-40', 'MA OS', 'ONE STOP DANBURY', 'OSWA 81-120', 'OSAP 1-40', 'TRANS 121-128', 'WVTH', 'OSCM 1-40', 'ONE STOP PCC', 'WACC', 'OS LIB', 'BROWDER', 'OS WESTERN', 'OS WALLACE', 'OSCS 1-40', 'MAIL ABSENTEE', 'LECC', 'OS DG', 'OSLH 81-120', 'OSNR 81-120', 'OSKD 1-40', 'OSRB 121-128', 'OS DENTON LIBRARY', 'OS POW', 'ABSEN 121-128', 'OS KTD', 'OS BOE', 'EAST OS', 'OSKD 81-120', 'OS COTC', 'OS FLETCHER', 'OSAB 81-120', 'TRANS 41-80', 'OSAV 1-40', 'OS ANGIER', 'OSAB 1-40', 'ECBL', 'OSHS 81-120', 'TAR HEEL MUNI BLD', 'ABSEN 1-40', 'OS BOE', 'OSBR 1-40', 'OS ARCADIA COMM BLDG', 'OSLL 81-120', 'OSWA 1-40', 'PROVIDENCE', 'CITY OS', 'OSLL 41-80', 'OSGR 121-128', 'OS ADMIN', 'OSAB 41-80', 'ELLERBE', 'OSGR 41-80', 'ABSEN 81-120', 'DOB OS', 'OS BR', 'ABSEN 41-80', 'OSWO 121-128', 'TRANS 81-120', 'OSCA 41-80', 'OSCA 81-120', 'OSWN 121-128', 'OSCS 121-128', 'ONE STOP ONE', 'OS ASU', 'OSBR 41-80', 'OSGR 1-40', 'HAMLET', 'OSHS 121-128', 'OSHS 41-80', 'OS NTP', 'OS LW', 'TARBORO 1', 'BELHAVEN OS', 'OSCM 81-120', 'OSTA 41-80', 'SMITHFIELD', 'OS LOBBY', 'OSLH 121-128', 'OSTA 81-120', 'OSOP 121-128', 'OSCM 121-128', 'OSZB 121-128', 'OSZB 1-40', 'PINES CHAP FELLSHIP HALL', 'OSCS 41-80', 'OS FSCO', 'OS ERWIN', 'OS BCR', 'OS GRANITE REC', 'WGSC', 'BENSON', 'OSWA 121-128', 'OSWN 1-40', 'PROVI 41-80', 'PROVI 81-120', 'OS BOE']
searchfor = searchfor+['MCGEE OS','OFFICE OS','ONE STOP CBR','ONE STOP EES']
searchfor = searchfor+['OS KENANSVILLE','OS JACKSON','OS HALIFAX','OS DTM','ONE STOP WALNUT COVE']
searchfor = searchfor+['OS A', 'OS B','OS CAB','OS CFCC','OS C','OS D','OS E','OS GVT','OS G','OS J','OS NLB','OS PVL']
searchfor = searchfor+['ABS ADDTNL', 'ABS BY MAIL','ABSEN','ARCHER LODGE OS','BLADEN BOE','CHADBOURN OS','CLAYTON OS','CURBSIDE','E COLUMBUS OS','ONE STOP 1','ONE STOP 2','ONE STOP 3','ONE STOP ADMIN','ONE STOP AG CENTER','ONE STOP ASU','ONE STOP BLOWING ROCK','ONE STOP CLY','ONE STOP COMMUNITY SCH','ONE STOP COUNTY OFFICE','ONE STOP DEEP GAP','ONE STOP ECU','ONE STOP ERWIN','ONE STOP FOSCOE','ONE STOP GASTON','ONE STOP GFR','ONE STOP LIB','ONE STOP LOBBY','ONE STOP LOB','ONE STOP MCSWAIN','ONE STOP MEAT CAMP','ONE STOP OCK','ONE STOP PFD','ONE STOP PINETOPS 3','ONE STOP POW','ONE STOP RC','ONE STOP RICH SQUARE','ONE STOP ROCKY MOUNT 2','ONE STOP TARBORO 1','ONE STOP WESTERN','ONE STOP WINTERVILLE','ONE STOP WWCC','ONESTOP-AVML','ONESTOP-BMBL','ONESTOP-COXE','ONESTOP-ECBL','ONESTOP-FVBL','ONESTOP-LCBL','ONESTOP-NABL','ONESTOP-SBBL','ONESTOP-WABL','ONESTOP-WVTH','OS AURORA','OS BELHAVEN','OS CAS','OS CUL','OS DTN','OS EAST','OS ERU','OS FESSENDEN ANNEX','OS GYM','OS KDH TOWN HALL','OS LINCOLN','OS LOC','OS OFF','OS MOUNT PLEASANT','OS MTO','OS MURFREE CENT','OS NASHVILLE','OS OFFICE','OS ROCKY MOUNT','OS WCU','OS WEST','OSAV','OSCA','OSCS','OSFV','OSHS','OSKD','OSLOB','OSME','OSNR','OSOP','OSRB','OSTA','PROVIDENCE OS','SMITHFIELD OS','TABOR CITY OS','TRANS']
searchfor = searchfor+['01-07A', '07-07A', '681', 'BLAN GROVE EMP CTR', 'BLDBORO SPAULD MON', 'CV', 'DALLAS', 'E ARC TWN HALL', 'FAIR', 'GATES BOE', 'GATES RURITAN CLUB', 'LIBRARY', 'LOBBY OS', 'LOB', 'MOUNT HOLLY', 'MX', 'ONE STOP HALIFAX', 'ONE STOP LITTLETON', 'ONE STOP SCOTLAND NECK', 'ONE STOP WELDON', 'PEM', 'REDS', 'STP']


In [28]:
#Subset the data
in_sos =  pivoted_election_results[pivoted_election_results["PRECINCT"].isin(searchfor)]
#Add a particular precinct to the votes to allocate (it's precinct name is the same as one in another county, and that one is a real precinct)
provi_wake = pivoted_election_results[pivoted_election_results['PREC_CO']=='PROVI_WAKE']
in_sos = pd.concat([in_sos,provi_wake])
in_sos = in_sos.groupby(by=["COUNTY"]).sum().reset_index()
display(in_sos)

PIVOT_COL        COUNTY  P20AGRDSMI  P20AGRDWAD  P20AGRDWAT  P20ATGRHAY  \
0              ALAMANCE         0.0         0.0         0.0         0.0   
1             ALLEGHANY         0.0         0.0         0.0         0.0   
2                  ASHE         0.0         0.0         0.0         0.0   
3                 AVERY         0.0         0.0         0.0         0.0   
4              BEAUFORT         0.0         0.0         0.0         0.0   
5                BERTIE         0.0         0.0         0.0         0.0   
6                BLADEN         0.0         0.0         0.0         0.0   
7              BUNCOMBE        22.0        55.0         2.0        17.0   
8              CABARRUS         0.0         0.0         0.0         0.0   
9              CALDWELL         0.0         0.0         0.0         0.0   
10               CAMDEN         0.0         0.0         0.0         0.0   
11               CHOWAN       198.0       205.0        37.0       203.0   
12             COLUMBUS       668.0       370.0       249.0       262.0   
13           CUMBERLAND      4664.0      5547.0      2398.0      1351.0   
14            CURRITUCK         0.0         0.0         0.0         0.0   
15                 DARE         6.0        10.0         2.0         3.0   
16             DAVIDSON         0.0         0.0         0.0         0.0   
17                DAVIE         0.0         0.0         0.0         0.0   
18               DUPLIN         0.0         0.0         0.0         0.0   
19               DURHAM        62.0       230.0        83.0        15.0   
20            EDGECOMBE         0.0         0.0         0.0         0.0   
21              FORSYTH      6361.0      9839.0      3568.0      1738.0   
22               GASTON      1850.0      2698.0       905.0      1574.0   
23                GATES       237.0       102.0        51.0        45.0   
24             GUILFORD         0.0         0.0         0.0         0.0   
25              HALIFAX       330.0       279.0       139.0        34.0   
26              HARNETT         0.0         0.0         0.0         0.0   
27              HAYWOOD         0.0         0.0         0.0         0.0   
28            HENDERSON        75.0        47.0        15.0        38.0   
29             HERTFORD         0.0         0.0         0.0         0.0   
30                 HYDE         0.0         0.0         0.0         0.0   
31              JACKSON         0.0         0.0         0.0         0.0   
32             JOHNSTON         0.0         0.0         0.0         0.0   
33                JONES         0.0         0.0         0.0         0.0   
34                  LEE         0.0         0.0         0.0         0.0   
35               LENOIR      1097.0       919.0       365.0       602.0   
36              LINCOLN         0.0         0.0         0.0         0.0   
37                MACON       483.0       777.0       131.0       545.0   
38               MARTIN         2.0         0.0         3.0         0.0   
39             MCDOWELL       365.0       586.0       113.0       704.0   
40          MECKLENBURG         0.0         0.0         0.0         0.0   
41                MOORE         0.0         0.0         0.0         0.0   
42                 NASH         0.0         0.0         0.0         0.0   
43          NEW HANOVER         6.0        15.0         7.0         9.0   
44          NORTHAMPTON         3.0         2.0         1.0         0.0   
45               ORANGE         0.0         0.0         0.0         0.0   
46              PAMLICO       185.0       257.0        71.0       204.0   
47           PASQUOTANK        10.0         9.0         3.0         2.0   
48           PERQUIMANS       227.0       108.0        35.0       145.0   
49                 PITT        32.0        21.0        12.0        14.0   
50                 POLK         0.0         0.0         0.0         0.0   
51             RICHMOND         0.0         0.0         0.0         0.0   
52              ROBESON  

### Perform the allocation

In [29]:
pivoted_copy = pivoted_election_results
#Remove county-wide results
election_results = pivoted_election_results[~pivoted_election_results["PRECINCT"].isin(searchfor)]
#remove the one precicnt specified above
election_results = election_results[election_results['PREC_CO']!='PROVI_WAKE']

#identify candidate race columns
races = []
for i in pivoted_copy.columns:
    if i.startswith('P'):
        if i.startswith('PREC'):
            continue
        else:
            races.append(i)
#allocation
election_results_allocated = allocate_absentee(election_results,in_sos,races,'COUNTY')
election_results_allocated.head()

C:\Users\SpencerNelson\Anaconda3\envs\rdh\lib\site-packages\pandas\core\indexing.py:1667: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider using pd.concat instead.  To get a de-fragmented frame, use `newframe = frame.copy()`
  self.obj[key] = value


PIVOT_COL      PREC_CO  P20AGRDSMI  P20AGRDWAD  P20AGRDWAT  P20ATGRHAY  \
0           0001_BURKE       135.0       159.0        27.0       126.0   
1           0003_BURKE        28.0        33.0        14.0        67.0   
2          0003_STANLY        83.0       128.0        35.0        67.0   
3          0007_STANLY        89.0        98.0        27.0        73.0   
4          0008_STANLY       108.0        95.0        98.0         9.0   

PIVOT_COL  P20ATGRMUM  P20ATGRONE  P20AUDDTOL  P20AUDDWOO  P20AUDRHOE  \
0               109.0       142.0        50.0       269.0       103.0   
1                52.0        74.0         9.0        64.0        44.0   
2                76.0       162.0        46.0       200.0        91.0   
3                81.0       141.0        32.0       193.0        85.0   
4                 7.0        14.0        73.0       228.0         3.0   

PIVOT_COL  P20AUDRSTR  P20GOVDBEA  P20GOVDCOO  P20GOVDDUY  P20GOVDHOL  \
0               247.0        62.0       306.0        52.0        83.0   
1               143.0        15.0        71.0         5.0        15.0   
2               186.0        26.0       251.0        54.0        60.0   
3               185.0        24.0       202.0        26.0        75.0   
4                26.0        44.0       272.0        11.0        90.0   

PIVOT_COL  P20GOVDNEW  P20GOVDREE  P20GOVDTHO  P20GOVDTOO  P20GOVRBEN  \
0                47.0        48.0        49.0        24.0         7.0   
1                 9.0        15.0        17.0        12.0         1.0   
2                20.0        41.0        52.0        35.0         6.0   
3                31.0        41.0        42.0        24.0         6.0   
4                23.0        72.0       105.0        24.0         0.0   

PIVOT_COL  P20GOVRCOC  P20GOVRELL  P20GOVRFOR  P20GOVRGEB  P20GOVRGRA  \
0                21.0         6.0       373.0        11.0        33.0   
1                10.0         5.0       186.0         1.0        16.0   
2                28.0        12.0       295.0        18.0        47.0   
3                16.0         3.0       292.0        18.0        32.0   
4                 2.0         0.0        24.0         3.0         5.0   

PIVOT_COL  P20GOVRJOH  P20GOVRRIT  P20GOVRROB  P20GOVRSTO  P20GOVRWEL  \
0                43.0        46.0       158.0        25.0        68.0   
1                19.0        19.0        89.0        16.0        32.0   
2                38.0        62.0        89.0        17.0        36.0   
3                35.0        50.0        99.0        37.0        38.0   
4                 2.0         3.0        19.0         1.0         0.0   

PIVOT_COL  P20INSRCAU  P20INSRPIE  P20LBRRDOB  P20LBRRFLO  P20LBRRSTA  \
0               207.0       149.0       144.0        56.0       156.0   
1               105.0        80.0        79.0        41.0        67.0   
2               190.0       105.0        94.0        69.0       115.0   
3               196.0        84.0       140.0        41.0       101.0   
4                11.0        18.0        16.0         3.0         7.0   

PIVOT_COL  P20PRECBLA  P20PRECKRA  P20PRECNPR  P20PREDBEN  P20PREDBID  \
0                 0.0         0.0         0.0         2.0       173.0   
1                 0.0         0.0         0.0         0.0        38.0   
2                 0.0         0.0         0.0         0.0       139.0   
3                 0.0         0.0         0.0         0.0       145.0   
4                 0.0         0.0         0.0         2.0       206.0   

PIVOT_COL  P20PREDBLO  P20PREDBOO  P20PREDBUT  P20PREDCAS  P20PREDDEL  \
0                44.0         1.0         8.0         0.0         2.0   
1                13.0         1.0         4.0         0.0         1.0   
2                49.0         0.0        12.0         0.0         0.0   
3                23.0         0.0         0.0         0.0         0.0   
4                31.0         0.0        23.0         1.0         0.0   

PIVOT_COL  P20PREDGAB  P20PREDKLO  P20PREDN

In [30]:
#Set all to integer
for i in pivoted_copy.columns:
    if i.startswith('P'):
        if i.startswith('PREC'):
            continue
        else:
            pivoted_copy[i] = pivoted_copy[i].astype(int)

In [31]:
#Verify the length of the allocated dataframe with prec gdf
print(len(election_results_allocated))
print(len(prec))

2666
2666


## Determine split precincts

In [32]:
#Instantiate variables
##DETERMINE WHAT PRECINCTS ARE SPLIT
er = election_results_allocated 
cong_splits = []
sldl_splits = []
sldu_splits = []
cong_split_count = 0
sldl_split_count = 0
sldu_split_count = 0
cong_split_dictionary = {}
sldu_split_dictionary = {}
sldl_split_dictionary = {}

cong_unsplit_dict = {}
sldu_unsplit_dict = {}
sldl_unsplit_dict = {}
no_dists = []

In [33]:
er.head()

PIVOT_COL      PREC_CO  P20AGRDSMI  P20AGRDWAD  P20AGRDWAT  P20ATGRHAY  \
0           0001_BURKE       135.0       159.0        27.0       126.0   
1           0003_BURKE        28.0        33.0        14.0        67.0   
2          0003_STANLY        83.0       128.0        35.0        67.0   
3          0007_STANLY        89.0        98.0        27.0        73.0   
4          0008_STANLY       108.0        95.0        98.0         9.0   

PIVOT_COL  P20ATGRMUM  P20ATGRONE  P20AUDDTOL  P20AUDDWOO  P20AUDRHOE  \
0               109.0       142.0        50.0       269.0       103.0   
1                52.0        74.0         9.0        64.0        44.0   
2                76.0       162.0        46.0       200.0        91.0   
3                81.0       141.0        32.0       193.0        85.0   
4                 7.0        14.0        73.0       228.0         3.0   

PIVOT_COL  P20AUDRSTR  P20GOVDBEA  P20GOVDCOO  P20GOVDDUY  P20GOVDHOL  \
0               247.0        62.0       306.0        52.0        83.0   
1               143.0        15.0        71.0         5.0        15.0   
2               186.0        26.0       251.0        54.0        60.0   
3               185.0        24.0       202.0        26.0        75.0   
4                26.0        44.0       272.0        11.0        90.0   

PIVOT_COL  P20GOVDNEW  P20GOVDREE  P20GOVDTHO  P20GOVDTOO  P20GOVRBEN  \
0                47.0        48.0        49.0        24.0         7.0   
1                 9.0        15.0        17.0        12.0         1.0   
2                20.0        41.0        52.0        35.0         6.0   
3                31.0        41.0        42.0        24.0         6.0   
4                23.0        72.0       105.0        24.0         0.0   

PIVOT_COL  P20GOVRCOC  P20GOVRELL  P20GOVRFOR  P20GOVRGEB  P20GOVRGRA  \
0                21.0         6.0       373.0        11.0        33.0   
1                10.0         5.0       186.0         1.0        16.0   
2                28.0        12.0       295.0        18.0        47.0   
3                16.0         3.0       292.0        18.0        32.0   
4                 2.0         0.0        24.0         3.0         5.0   

PIVOT_COL  P20GOVRJOH  P20GOVRRIT  P20GOVRROB  P20GOVRSTO  P20GOVRWEL  \
0                43.0        46.0       158.0        25.0        68.0   
1                19.0        19.0        89.0        16.0        32.0   
2                38.0        62.0        89.0        17.0        36.0   
3                35.0        50.0        99.0        37.0        38.0   
4                 2.0         3.0        19.0         1.0         0.0   

PIVOT_COL  P20INSRCAU  P20INSRPIE  P20LBRRDOB  P20LBRRFLO  P20LBRRSTA  \
0               207.0       149.0       144.0        56.0       156.0   
1               105.0        80.0        79.0        41.0        67.0   
2               190.0       105.0        94.0        69.0       115.0   
3               196.0        84.0       140.0        41.0       101.0   
4                11.0        18.0        16.0         3.0         7.0   

PIVOT_COL  P20PRECBLA  P20PRECKRA  P20PRECNPR  P20PREDBEN  P20PREDBID  \
0                 0.0         0.0         0.0         2.0       173.0   
1                 0.0         0.0         0.0         0.0        38.0   
2                 0.0         0.0         0.0         0.0       139.0   
3                 0.0         0.0         0.0         0.0       145.0   
4                 0.0         0.0         0.0         2.0       206.0   

PIVOT_COL  P20PREDBLO  P20PREDBOO  P20PREDBUT  P20PREDCAS  P20PREDDEL  \
0                44.0         1.0         8.0         0.0         2.0   
1                13.0         1.0         4.0         0.0         1.0   
2                49.0         0.0        12.0         0.0         0.0   
3                23.0         0.0         0.0         0.0         0.0   
4                31.0         0.0        23.0         1.0         0.0   

PIVOT_COL  P20PREDGAB  P20PREDKLO  P20PREDN

In [34]:
for i in er['PREC_CO']:
    sub = er[er['PREC_CO']==i]
    cong = []
    sldl = []
    sldu = []
    for col in sub.columns:
        if col.startswith('P'):
            if col.startswith('PREC'):
                continue
            else:
                col_sum = sub[col].sum()
                if int(col_sum)!= 0:
                    if 'PCON' in str(col):
                        cong_dist = str(col).replace('PCON','')[:2]
                        cong.append(cong_dist)
                    elif 'PSU' in str(col):
                        sldu_dist = str(col).replace('PSU','')[:2]
                        sldu.append(sldu_dist)
                    elif 'PSL' in str(col):
                        sldl_dist = str(col).replace('PSL','')[:3]
                        sldl.append(sldl_dist)
                    else:
                        continue
    cong = list(set(cong))
    sldl = list(set(sldl))
    sldu = list(set(sldu))
    if len(cong)>1:
        print(i, ' is split by congressional district. It is in districts: ', ', '.join(cong))
        cong_splits.append(i)
        cong_split_count+=1
        cong_split_dictionary.update({i:cong})
    if len(cong)==1:
        cong_unsplit_dict.update({i:cong[0]})
    if len(cong) == 0:
        no_dists.append(i)
    if len(sldl)> 1:
        print(i, ' is split by State House district. It is in districts: ', ', '.join(sldl))
        sldl_splits.append(i)
        sldl_split_count+=1
        sldl_split_dictionary.update({i:sldl})
    if len(sldl)==0:
        no_dists.append(i)
    if len(sldl)==1:
        sldl_unsplit_dict.update({i:sldl[0]})
    if len(sldu)> 1:
        print(i, ' is split by State Senate districts. It is in districts: ', ', '.join(sldu))
        sldu_splits.append(i)
        sldu_split_count+=1
        sldu_split_dictionary.update({i:sldu})
    if len(sldu)==0:
        no_dists.append(i)
    if len(sldu)==1:
        sldu_unsplit_dict.update({i:sldu[0]})
no_dists = list(set(no_dists))
print('****************************************************')
print('Congressional split count: ', str(cong_split_count))
print(cong_split_dictionary)
print('SLDU split count: ', str(sldu_split_count))
print(sldu_split_dictionary)
print('SLDL split count: ', str(sldl_split_count))
print(sldl_split_dictionary)
print('***************************************************')
#print('There are NO districts associated with the following precincts: ', sorted(no_dists))
print('There are ', str(len(no_dists)), ' that are NOT assigned to a district.')
print('There are ', str(len(prec)), ' in the Precinct shapefile.')
print('There are ', str(len(er)), ' in the allocated election results file.')
diff = len(er)-len(prec)
if diff==len(no_dists):
    print('The no district list is same length as difference between ER and Precinct shapefile: ', str(diff))
else:
    print('The no district lenght is: ', str(len(no_dists)))
    print('The difference between precinct shapefile and ER is: ', str(diff))
    print('The difference between the values is: ', str(diff-len(no_dists)))

062_FORSYTH  is split by congressional district. It is in districts:  10, 06
096_MECKLENBURG  is split by congressional district. It is in districts:  12, 09
10-03_WAKE  is split by congressional district. It is in districts:  02, 04
12-13_CABARRUS  is split by State House district. It is in districts:  082, 083
15-01_WAKE  is split by State House district. It is in districts:  033, 037
15-02_WAKE  is split by State House district. It is in districts:  033, 036
1513B_PITT  is split by State House district. It is in districts:  009, 012
217_MECKLENBURG  is split by congressional district. It is in districts:  12, 09
218_MECKLENBURG  is split by congressional district. It is in districts:  12, 09
30_CATAWBA  is split by congressional district. It is in districts:  05, 10
30_RUTHERFORD  is split by congressional district. It is in districts:  11, 05
37_CATAWBA  is split by congressional district. It is in districts:  05, 10
AH49_CUMBERLAND  is split by State House district. It is in distr

In [35]:
## Verify with Precinct shapefile again
prec['MATCH'] = prec.apply(lambda x: '_'.join([x['prec_id'],x['county_nam']]),axis=1)
er['MATCH'] = er['PREC_CO'].apply(lambda x: str(x))
join = pd.merge(prec,er, on = 'MATCH',how='outer',indicator=True)
print(len(join))
print(len(prec))
print(len(er))
print(join['_merge'].unique())
prec_only = list(join[join['_merge']=='left_only']['MATCH'])
er_only = list(join[join['_merge']=='right_only']['MATCH'])
print(er_only)
print(prec_only)
print(len(er_only))
print(len(prec_only))

2666
2666
2666
['both']
Categories (3, object): ['left_only', 'right_only', 'both']
[]
[]
0
0


<ipython-input-35-02432206fd33>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  er['MATCH'] = er['PREC_CO'].apply(lambda x: str(x))


### Separate the data into three dataframes

In [36]:
congress_cols = []
sldu_cols = []
sldl_cols = []
for i in er.columns:
    if i.startswith('PCON'):
        congress_cols.append(i)
    elif i.startswith('PSL'):
        sldl_cols.append(i)
    elif i.startswith('P20'):
        sldu_cols.append(i)
    elif i.startswith('PSU'):
        sldu_cols.append(i)
    else:
        congress_cols.append(i)
        sldu_cols.append(i)
        sldl_cols.append(i)
cong_df = er[congress_cols]
sldu_df = er[sldu_cols]
sldl_df = er[sldl_cols]

display(cong_df.head())
display(sldu_df.head())
display(sldl_df.head())

PIVOT_COL      PREC_CO  PCON01RBAC  PCON01RGLI  PCON01RNIX  PCON01RSMI  \
0           0001_BURKE         0.0         0.0         0.0         0.0   
1           0003_BURKE         0.0         0.0         0.0         0.0   
2          0003_STANLY         0.0         0.0         0.0         0.0   
3          0007_STANLY         0.0         0.0         0.0         0.0   
4          0008_STANLY         0.0         0.0         0.0         0.0   

PIVOT_COL  PCON02DJOH  PCON02DNEL  PCON02DROS  PCON02DTER  PCON04DLOC  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PCON04DPRI  PCON04RLOO  PCON04RSAR  PCON04RSHA  PCON04RTHO  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PCON05DBRO  PCON05DHUG  PCON06DDAV  PCON06DFOX  PCON06DHAN  \
0               195.0       119.0         0.0         0.0         0.0   
1                43.0        32.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PCON06DMAN  PCON06DMON  PCON06RHAY  PCON06RPIC  PCON07DCOL  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PCON07DJUD  PCON07DWAR  PCON09DBRO  PCON09DSOU  PCON09DWAL  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PCON09DWIL  PCON10RJOH  PCON10RMCH  PCON10RWAL  PCON11DCOL  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PCON11DDAV  PCON11DOSH  PCON11DPRI  PCON11DWOO  PCON11RARC  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PCON11RBEN  PCON11RBUR  PCON11RCAW  PCON11RDAV  PCON11RDRI  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PCON11RFEK  PCON11RGEN  PCON11RK

PIVOT_COL      PREC_CO  P20AGRDSMI  P20AGRDWAD  P20AGRDWAT  P20ATGRHAY  \
0           0001_BURKE       135.0       159.0        27.0       126.0   
1           0003_BURKE        28.0        33.0        14.0        67.0   
2          0003_STANLY        83.0       128.0        35.0        67.0   
3          0007_STANLY        89.0        98.0        27.0        73.0   
4          0008_STANLY       108.0        95.0        98.0         9.0   

PIVOT_COL  P20ATGRMUM  P20ATGRONE  P20AUDDTOL  P20AUDDWOO  P20AUDRHOE  \
0               109.0       142.0        50.0       269.0       103.0   
1                52.0        74.0         9.0        64.0        44.0   
2                76.0       162.0        46.0       200.0        91.0   
3                81.0       141.0        32.0       193.0        85.0   
4                 7.0        14.0        73.0       228.0         3.0   

PIVOT_COL  P20AUDRSTR  P20GOVDBEA  P20GOVDCOO  P20GOVDDUY  P20GOVDHOL  \
0               247.0        62.0       306.0        52.0        83.0   
1               143.0        15.0        71.0         5.0        15.0   
2               186.0        26.0       251.0        54.0        60.0   
3               185.0        24.0       202.0        26.0        75.0   
4                26.0        44.0       272.0        11.0        90.0   

PIVOT_COL  P20GOVDNEW  P20GOVDREE  P20GOVDTHO  P20GOVDTOO  P20GOVRBEN  \
0                47.0        48.0        49.0        24.0         7.0   
1                 9.0        15.0        17.0        12.0         1.0   
2                20.0        41.0        52.0        35.0         6.0   
3                31.0        41.0        42.0        24.0         6.0   
4                23.0        72.0       105.0        24.0         0.0   

PIVOT_COL  P20GOVRCOC  P20GOVRELL  P20GOVRFOR  P20GOVRGEB  P20GOVRGRA  \
0                21.0         6.0       373.0        11.0        33.0   
1                10.0         5.0       186.0         1.0        16.0   
2                28.0        12.0       295.0        18.0        47.0   
3                16.0         3.0       292.0        18.0        32.0   
4                 2.0         0.0        24.0         3.0         5.0   

PIVOT_COL  P20GOVRJOH  P20GOVRRIT  P20GOVRROB  P20GOVRSTO  P20GOVRWEL  \
0                43.0        46.0       158.0        25.0        68.0   
1                19.0        19.0        89.0        16.0        32.0   
2                38.0        62.0        89.0        17.0        36.0   
3                35.0        50.0        99.0        37.0        38.0   
4                 2.0         3.0        19.0         1.0         0.0   

PIVOT_COL  P20INSRCAU  P20INSRPIE  P20LBRRDOB  P20LBRRFLO  P20LBRRSTA  \
0               207.0       149.0       144.0        56.0       156.0   
1               105.0        80.0        79.0        41.0        67.0   
2               190.0       105.0        94.0        69.0       115.0   
3               196.0        84.0       140.0        41.0       101.0   
4                11.0        18.0        16.0         3.0         7.0   

PIVOT_COL  P20PRECBLA  P20PRECKRA  P20PRECNPR  P20PREDBEN  P20PREDBID  \
0                 0.0         0.0         0.0         2.0       173.0   
1                 0.0         0.0         0.0         0.0        38.0   
2                 0.0         0.0         0.0         0.0       139.0   
3                 0.0         0.0         0.0         0.0       145.0   
4                 0.0         0.0         0.0         2.0       206.0   

PIVOT_COL  P20PREDBLO  P20PREDBOO  P20PREDBUT  P20PREDCAS  P20PREDDEL  \
0                44.0         1.0         8.0         0.0         2.0   
1                13.0         1.0         4.0         0.0         1.0   
2                49.0         0.0        12.0         0.0         0.0   
3                23.0         0.0         0.0         0.0         0.0   
4                31.0         0.0        23.0         1.0         0.0   

PIVOT_COL  P20PREDGAB  P20PREDKLO  P20PREDN

PIVOT_COL      PREC_CO  PSL003RKOH  PSL003RQUE  PSL003RSMI  PSL003RTYS  \
0           0001_BURKE         0.0         0.0         0.0         0.0   
1           0003_BURKE         0.0         0.0         0.0         0.0   
2          0003_STANLY         0.0         0.0         0.0         0.0   
3          0007_STANLY         0.0         0.0         0.0         0.0   
4          0008_STANLY         0.0         0.0         0.0         0.0   

PIVOT_COL  PSL005DHUN  PSL005DRIV  PSL006RHAN  PSL006RROL  PSL009DFAR  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PSL009DHOC  PSL012DBRE  PSL012DBRO  PSL012DCOX  PSL014RCLE  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PSL014REDW  PSL015RPRI  PSL015RSHE  PSL019DDAW  PSL019DMOR  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PSL019RMIL  PSL019RPER  PSL020RDAV  PSL020RLAN  PSL021DPEA  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PSL021DSMI  PSL022DDEN  PSL022DKIR  PSL024DFAR  PSL024DMCN  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PSL025RCHE  PSL025RMAT  PSL026RTAT  PSL026RWHI  PSL027DHIC  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PSL027DMCD  PSL027DWRA  PSL033DGIL  PSL033DMAR  PSL035RCAN  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PSL035RPET  PSL036RCOL  PSL036RPAG  PSL037RMOO  PSL037RPAR  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PSL037RPOW  PSL038DEDW  PSL038DJ

## Process State Senate file

In [37]:
sldu_df['SLDU_DIST'] = sldu_df['PREC_CO'].apply(lambda x: sldu_unsplit_dict.get(x))
sldu_df.head()

<ipython-input-37-53e1f1dc68a3>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sldu_df['SLDU_DIST'] = sldu_df['PREC_CO'].apply(lambda x: sldu_unsplit_dict.get(x))


PIVOT_COL      PREC_CO  P20AGRDSMI  P20AGRDWAD  P20AGRDWAT  P20ATGRHAY  \
0           0001_BURKE       135.0       159.0        27.0       126.0   
1           0003_BURKE        28.0        33.0        14.0        67.0   
2          0003_STANLY        83.0       128.0        35.0        67.0   
3          0007_STANLY        89.0        98.0        27.0        73.0   
4          0008_STANLY       108.0        95.0        98.0         9.0   

PIVOT_COL  P20ATGRMUM  P20ATGRONE  P20AUDDTOL  P20AUDDWOO  P20AUDRHOE  \
0               109.0       142.0        50.0       269.0       103.0   
1                52.0        74.0         9.0        64.0        44.0   
2                76.0       162.0        46.0       200.0        91.0   
3                81.0       141.0        32.0       193.0        85.0   
4                 7.0        14.0        73.0       228.0         3.0   

PIVOT_COL  P20AUDRSTR  P20GOVDBEA  P20GOVDCOO  P20GOVDDUY  P20GOVDHOL  \
0               247.0        62.0       306.0        52.0        83.0   
1               143.0        15.0        71.0         5.0        15.0   
2               186.0        26.0       251.0        54.0        60.0   
3               185.0        24.0       202.0        26.0        75.0   
4                26.0        44.0       272.0        11.0        90.0   

PIVOT_COL  P20GOVDNEW  P20GOVDREE  P20GOVDTHO  P20GOVDTOO  P20GOVRBEN  \
0                47.0        48.0        49.0        24.0         7.0   
1                 9.0        15.0        17.0        12.0         1.0   
2                20.0        41.0        52.0        35.0         6.0   
3                31.0        41.0        42.0        24.0         6.0   
4                23.0        72.0       105.0        24.0         0.0   

PIVOT_COL  P20GOVRCOC  P20GOVRELL  P20GOVRFOR  P20GOVRGEB  P20GOVRGRA  \
0                21.0         6.0       373.0        11.0        33.0   
1                10.0         5.0       186.0         1.0        16.0   
2                28.0        12.0       295.0        18.0        47.0   
3                16.0         3.0       292.0        18.0        32.0   
4                 2.0         0.0        24.0         3.0         5.0   

PIVOT_COL  P20GOVRJOH  P20GOVRRIT  P20GOVRROB  P20GOVRSTO  P20GOVRWEL  \
0                43.0        46.0       158.0        25.0        68.0   
1                19.0        19.0        89.0        16.0        32.0   
2                38.0        62.0        89.0        17.0        36.0   
3                35.0        50.0        99.0        37.0        38.0   
4                 2.0         3.0        19.0         1.0         0.0   

PIVOT_COL  P20INSRCAU  P20INSRPIE  P20LBRRDOB  P20LBRRFLO  P20LBRRSTA  \
0               207.0       149.0       144.0        56.0       156.0   
1               105.0        80.0        79.0        41.0        67.0   
2               190.0       105.0        94.0        69.0       115.0   
3               196.0        84.0       140.0        41.0       101.0   
4                11.0        18.0        16.0         3.0         7.0   

PIVOT_COL  P20PRECBLA  P20PRECKRA  P20PRECNPR  P20PREDBEN  P20PREDBID  \
0                 0.0         0.0         0.0         2.0       173.0   
1                 0.0         0.0         0.0         0.0        38.0   
2                 0.0         0.0         0.0         0.0       139.0   
3                 0.0         0.0         0.0         0.0       145.0   
4                 0.0         0.0         0.0         2.0       206.0   

PIVOT_COL  P20PREDBLO  P20PREDBOO  P20PREDBUT  P20PREDCAS  P20PREDDEL  \
0                44.0         1.0         8.0         0.0         2.0   
1                13.0         1.0         4.0         0.0         1.0   
2                49.0         0.0        12.0         0.0         0.0   
3                23.0         0.0         0.0         0.0         0.0   
4                31.0         0.0        23.0         1.0         0.0   

PIVOT_COL  P20PREDGAB  P20PREDKLO  P20PREDN

In [38]:
for i in sldu_df.columns:
    if i.startswith('P'):
        if i.startswith('PREC'):
            continue
        else:
            sldu_df[i] = sldu_df[i].astype(int)
sldu_df.head()

<ipython-input-38-31ca8c235173>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sldu_df[i] = sldu_df[i].astype(int)


PIVOT_COL      PREC_CO  P20AGRDSMI  P20AGRDWAD  P20AGRDWAT  P20ATGRHAY  \
0           0001_BURKE         135         159          27         126   
1           0003_BURKE          28          33          14          67   
2          0003_STANLY          83         128          35          67   
3          0007_STANLY          89          98          27          73   
4          0008_STANLY         108          95          98           9   

PIVOT_COL  P20ATGRMUM  P20ATGRONE  P20AUDDTOL  P20AUDDWOO  P20AUDRHOE  \
0                 109         142          50         269         103   
1                  52          74           9          64          44   
2                  76         162          46         200          91   
3                  81         141          32         193          85   
4                   7          14          73         228           3   

PIVOT_COL  P20AUDRSTR  P20GOVDBEA  P20GOVDCOO  P20GOVDDUY  P20GOVDHOL  \
0                 247          62         306          52          83   
1                 143          15          71           5          15   
2                 186          26         251          54          60   
3                 185          24         202          26          75   
4                  26          44         272          11          90   

PIVOT_COL  P20GOVDNEW  P20GOVDREE  P20GOVDTHO  P20GOVDTOO  P20GOVRBEN  \
0                  47          48          49          24           7   
1                   9          15          17          12           1   
2                  20          41          52          35           6   
3                  31          41          42          24           6   
4                  23          72         105          24           0   

PIVOT_COL  P20GOVRCOC  P20GOVRELL  P20GOVRFOR  P20GOVRGEB  P20GOVRGRA  \
0                  21           6         373          11          33   
1                  10           5         186           1          16   
2                  28          12         295          18          47   
3                  16           3         292          18          32   
4                   2           0          24           3           5   

PIVOT_COL  P20GOVRJOH  P20GOVRRIT  P20GOVRROB  P20GOVRSTO  P20GOVRWEL  \
0                  43          46         158          25          68   
1                  19          19          89          16          32   
2                  38          62          89          17          36   
3                  35          50          99          37          38   
4                   2           3          19           1           0   

PIVOT_COL  P20INSRCAU  P20INSRPIE  P20LBRRDOB  P20LBRRFLO  P20LBRRSTA  \
0                 207         149         144          56         156   
1                 105          80          79          41          67   
2                 190         105          94          69         115   
3                 196          84         140          41         101   
4                  11          18          16           3           7   

PIVOT_COL  P20PRECBLA  P20PRECKRA  P20PRECNPR  P20PREDBEN  P20PREDBID  \
0                   0           0           0           2         173   
1                   0           0           0           0          38   
2                   0           0           0           0         139   
3                   0           0           0           0         145   
4                   0           0           0           2         206   

PIVOT_COL  P20PREDBLO  P20PREDBOO  P20PREDBUT  P20PREDCAS  P20PREDDEL  \
0                  44           1           8           0           2   
1                  13           1           4           0           1   
2                  49           0          12           0           0   
3                  23           0           0           0           0   
4                  31           0          23           1           0   

PIVOT_COL  P20PREDGAB  P20PREDKLO  P20PREDN

In [39]:
display(prec.head())
prec_cols = list(prec.columns)
new_prec_cols = [i.upper() for i in prec_cols]
new_prec_cols.remove('GEOMETRY')
new_prec_cols[-1] = 'geometry'
prec_cols_dict = dict(zip(prec_cols,new_prec_cols))
prec.rename(columns = prec_cols_dict,inplace=True)
prec.head()

id prec_id                      enr_desc county_nam of_prec_id  county_id  \
0   1      14           14_Y E SMITH SCHOOL     DURHAM       None         32   
1   2    EMIS             EMIS_EMERALD ISLE   CARTERET       None         16   
2   3     131  131_VIENNA ELEMENTARY SCHOOL    FORSYTH       None         34   
3   4      MM            MM_MORVEN/MCFARLAN      ANSON       None          4   
4   5    CRDL                   CRDL_CREDLE  GRANVILLE       None         39   

  blockid                                           geometry           MATCH  
0    None  POLYGON ((2043445.004 806092.205, 2043253.389 ...       14_DURHAM  
1    None  POLYGON ((2566809.355 312013.723, 2567226.337 ...   EMIS_CARTERET  
2    None  POLYGON ((1580533.350 868933.766, 1580723.583 ...     131_FORSYTH  
3    None  POLYGON ((1720554.155 385895.605, 1720464.104 ...        MM_ANSON  
4    None  POLYGON ((2115518.562 932754.945, 2115429.276 ...  CRDL_GRANVILLE

ID PREC_ID                      ENR_DESC COUNTY_NAM OF_PREC_ID  COUNTY_ID  \
0   1      14           14_Y E SMITH SCHOOL     DURHAM       None         32   
1   2    EMIS             EMIS_EMERALD ISLE   CARTERET       None         16   
2   3     131  131_VIENNA ELEMENTARY SCHOOL    FORSYTH       None         34   
3   4      MM            MM_MORVEN/MCFARLAN      ANSON       None          4   
4   5    CRDL                   CRDL_CREDLE  GRANVILLE       None         39   

  BLOCKID                                           geometry           MATCH  
0    None  POLYGON ((2043445.004 806092.205, 2043253.389 ...       14_DURHAM  
1    None  POLYGON ((2566809.355 312013.723, 2567226.337 ...   EMIS_CARTERET  
2    None  POLYGON ((1580533.350 868933.766, 1580723.583 ...     131_FORSYTH  
3    None  POLYGON ((1720554.155 385895.605, 1720464.104 ...        MM_ANSON  
4    None  POLYGON ((2115518.562 932754.945, 2115429.276 ...  CRDL_GRANVILLE

In [40]:
sldu_prec = pd.merge(prec,sldu_df,on='MATCH',how = 'outer', indicator = True)
display(sldu_prec[sldu_prec['_merge']!='both'])

Empty GeoDataFrame
Columns: [ID, PREC_ID, ENR_DESC, COUNTY_NAM, OF_PREC_ID, COUNTY_ID, BLOCKID, geometry, MATCH, PREC_CO, P20AGRDSMI, P20AGRDWAD, P20AGRDWAT, P20ATGRHAY, P20ATGRMUM, P20ATGRONE, P20AUDDTOL, P20AUDDWOO, P20AUDRHOE, P20AUDRSTR, P20GOVDBEA, P20GOVDCOO, P20GOVDDUY, P20GOVDHOL, P20GOVDNEW, P20GOVDREE, P20GOVDTHO, P20GOVDTOO, P20GOVRBEN, P20GOVRCOC, P20GOVRELL, P20GOVRFOR, P20GOVRGEB, P20GOVRGRA, P20GOVRJOH, P20GOVRRIT, P20GOVRROB, P20GOVRSTO, P20GOVRWEL, P20INSRCAU, P20INSRPIE, P20LBRRDOB, P20LBRRFLO, P20LBRRSTA, P20PRECBLA, P20PRECKRA, P20PRECNPR, P20PREDBEN, P20PREDBID, P20PREDBLO, P20PREDBOO, P20PREDBUT, P20PREDCAS, P20PREDDEL, P20PREDGAB, P20PREDKLO, P20PREDNPR, P20PREDPAT, P20PREDSAN, P20PREDSTE, P20PREDWAR, P20PREDWIL, P20PREDYAN, P20PREGHAW, P20PREGNPR, P20PRELABR, P20PRELARM, P20PRELBEH, P20PRELBLE, P20PRELFAA, P20PRELGER, P20PRELHIL, P20PRELHOR, P20PRELJOR, P20PRELKOK, P20PRELMCA, P20PRELNPR, P20PRELOGL, P20PRELRIC, P20PRELRUF, P20PRELSUP, P20PRELVOH, P20PRENNPR, P20PRERNPR, P20PRERTRU, P20PRERWAL, P20PRERWEL, P20SOSRBRO, P20SOSRLAP, P20SOSRSYK, P20SPIDBAR, P20SPIDJOH, P20SPIDMAH, P20SPIDMAN, P20SPIDSUT, P20SPIRHOR, P20SPIRTRU, P20TREDAJM, P20TREDCHA, P20TREDLEA, ...]
Index: []

In [41]:
sldu_prec.drop(columns = ['BLOCKID','OF_PREC_ID','ID','PREC_CO','PRECINCT','COUNTY','_merge'],inplace=True)
sldu_prec.rename(columns = {'MATCH':'UNIQUE_ID'},inplace=True)
sldu_prec['COUNTY_ID'] = sldu_prec['COUNTY_ID'].astype(str)
sldu_prec['COUNTYFP'] = sldu_prec['COUNTY_ID'].apply(lambda x: str(x).zfill(3))
sldu_prec.head()

PREC_ID                      ENR_DESC COUNTY_NAM COUNTY_ID  \
0      14           14_Y E SMITH SCHOOL     DURHAM        32   
1    EMIS             EMIS_EMERALD ISLE   CARTERET        16   
2     131  131_VIENNA ELEMENTARY SCHOOL    FORSYTH        34   
3      MM            MM_MORVEN/MCFARLAN      ANSON         4   
4    CRDL                   CRDL_CREDLE  GRANVILLE        39   

                                            geometry       UNIQUE_ID  \
0  POLYGON ((2043445.004 806092.205, 2043253.389 ...       14_DURHAM   
1  POLYGON ((2566809.355 312013.723, 2567226.337 ...   EMIS_CARTERET   
2  POLYGON ((1580533.350 868933.766, 1580723.583 ...     131_FORSYTH   
3  POLYGON ((1720554.155 385895.605, 1720464.104 ...        MM_ANSON   
4  POLYGON ((2115518.562 932754.945, 2115429.276 ...  CRDL_GRANVILLE   

   P20AGRDSMI  P20AGRDWAD  P20AGRDWAT  P20ATGRHAY  P20ATGRMUM  P20ATGRONE  \
0          92         342         109           2           6           3   
1         116         290          27         133         353         267   
2         140         281          75          75          83         261   
3          89         228          56           7          21          13   
4         217         148          60          40          18          39   

   P20AUDDTOL  P20AUDDWOO  P20AUDRHOE  P20AUDRSTR  P20GOVDBEA  P20GOVDCOO  \
0         270         283           6           8         126         528   
1          46         406         462         260          52         503   
2         113         400         158         217          69         526   
3          34         334          12          23          56         356   
4          81         367          48          45          41         418   

   P20GOVDDUY  P20GOVDHOL  P20GOVDNEW  P20GOVDREE  P20GOVDTHO  P20GOVDTOO  \
0          20          91          20          45         277          31   
1         102         128          14          43         139          36   
2          93         197          20          91          74          53   
3         176          44          25          35          48          10   
4          66         150          32          57         102          47   

   P20GOVRBEN  P20GOVRCOC  P20GOVRELL  P20GOVRFOR  P20GOVRGEB  P20GOVRGRA  \
0           0           2           2          12           1           4   
1          66          39          49         724          41          83   
2          12          34          21         378          25          62   
3           0           7           0          41           0           3   
4           0           9          12          94           8           8   

   P20GOVRJOH  P20GOVRRIT  P20GOVRROB  P20GOVRSTO  P20GOVRWEL  P20INSRCAU  \
0           1           2           1           0           9          10   
1          39          72         387          22          54         575   
2          67          58         103          36          57         261   
3          12           2          12           6           2          21   
4           9          12          23           8          18          55   

   P20INSRPIE  P20LBRRDOB  P20LBRRFLO  P20LBRRSTA  P20PRECBLA  P20PRECKRA  \
0           5           4           3           4           0           3   
1         154         173         348         210           0           0   
2         129         145          67         175           0           0   
3          16          13           6          20           0           0   
4          40          31          19          46           0           0   

   P20PRECNPR  P20PREDBEN  P20PREDBID  P20PREDBLO  P20PREDBOO  P20PREDBUT  \
0           0           2         270          39           2           3   
1           0           0         257         114           0          27   
2           0           0         251         101           0          63   
3           0           3         263          30           1           4   
4           0        

In [42]:
sldu_order = [i for i in sldu_prec.columns]
sldu_order.remove('geometry')
sldu_order.remove('UNIQUE_ID')
sldu_order.remove('COUNTYFP')
sldu_order.append('geometry')
sldu_order.remove('SLDU_DIST')
sldu_order[4:4] = ['SLDU_DIST']
sldu_order[0:1] = ['UNIQUE_ID','COUNTYFP']

In [43]:
sldu_prec_df = sldu_prec[sldu_order]
sldu_prec_df['SLDU_DIST'] = sldu_prec_df['SLDU_DIST'].astype(str)
sldu_prec_df['SLDU_DIST'] = sldu_prec_df['SLDU_DIST'].apply(lambda x: 'n/a' if x in ['nan','None']  else x)
sldu_prec_df.head()

C:\Users\SpencerNelson\Anaconda3\envs\rdh\lib\site-packages\geopandas\geodataframe.py:1322: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super(GeoDataFrame, self).__setitem__(key, value)


UNIQUE_ID COUNTYFP                      ENR_DESC COUNTY_NAM COUNTY_ID  \
0       14_DURHAM      032           14_Y E SMITH SCHOOL     DURHAM        32   
1   EMIS_CARTERET      016             EMIS_EMERALD ISLE   CARTERET        16   
2     131_FORSYTH      034  131_VIENNA ELEMENTARY SCHOOL    FORSYTH        34   
3        MM_ANSON      004            MM_MORVEN/MCFARLAN      ANSON         4   
4  CRDL_GRANVILLE      039                   CRDL_CREDLE  GRANVILLE        39   

  SLDU_DIST  P20AGRDSMI  P20AGRDWAD  P20AGRDWAT  P20ATGRHAY  P20ATGRMUM  \
0        20          92         342         109           2           6   
1       n/a         116         290          27         133         353   
2       n/a         140         281          75          75          83   
3       n/a          89         228          56           7          21   
4       n/a         217         148          60          40          18   

   P20ATGRONE  P20AUDDTOL  P20AUDDWOO  P20AUDRHOE  P20AUDRSTR  P20GOVDBEA  \
0           3         270         283           6           8         126   
1         267          46         406         462         260          52   
2         261         113         400         158         217          69   
3          13          34         334          12          23          56   
4          39          81         367          48          45          41   

   P20GOVDCOO  P20GOVDDUY  P20GOVDHOL  P20GOVDNEW  P20GOVDREE  P20GOVDTHO  \
0         528          20          91          20          45         277   
1         503         102         128          14          43         139   
2         526          93         197          20          91          74   
3         356         176          44          25          35          48   
4         418          66         150          32          57         102   

   P20GOVDTOO  P20GOVRBEN  P20GOVRCOC  P20GOVRELL  P20GOVRFOR  P20GOVRGEB  \
0          31           0           2           2          12           1   
1          36          66          39          49         724          41   
2          53          12          34          21         378          25   
3          10           0           7           0          41           0   
4          47           0           9          12          94           8   

   P20GOVRGRA  P20GOVRJOH  P20GOVRRIT  P20GOVRROB  P20GOVRSTO  P20GOVRWEL  \
0           4           1           2           1           0           9   
1          83          39          72         387          22          54   
2          62          67          58         103          36          57   
3           3          12           2          12           6           2   
4           8           9          12          23           8          18   

   P20INSRCAU  P20INSRPIE  P20LBRRDOB  P20LBRRFLO  P20LBRRSTA  P20PRECBLA  \
0          10           5           4           3           4           0   
1         575         154         173         348         210           0   
2         261         129         145          67         175           0   
3          21          16          13           6          20           0   
4          55          40          31          19          46           0   

   P20PRECKRA  P20PRECNPR  P20PREDBEN  P20PREDBID  P20PREDBLO  P20PREDBOO  \
0           3           0           2         270          39           2   
1           0           0           0         257         114           0   
2           0           0           0         251         101           0   
3           0           0           3         263          30           1   
4           0           0           2         234          81           4   

   P20PREDBUT  P20PREDCAS  P20PREDDEL  P20PREDGAB  P20PREDKLO  P20PREDNPR  \
0           3           0           0           1           7           0   
1          27           0           0           4          23           9   
2          63           1           0           4           0

In [44]:
sldu_prec_df.to_file('./nc_prim_20_st_sldu_prec.shp')

## Process Congressional dataframe

In [45]:
### READ IN THE CONGRESSSIONAL FILE
districts = os.path.join(source_files, 'district_bounds')
congress_folder = os.path.join(districts,'congress')
congress_shp = gp.read_file(os.path.join(congress_folder,'C-Goodwin-A-1-TC.shp'))
congress_shp.head()

DISTRICT  POPULATION                                           geometry
0       12      733499  POLYGON ((449362.059 184483.802, 449368.426 18...
1        2      733499  POLYGON ((622633.549 201431.242, 622384.873 20...
2        3      733499  POLYGON ((773148.847 217156.853, 773146.315 21...
3        1      733498  POLYGON ((747975.917 187057.151, 747789.630 18...
4        4      733499  POLYGON ((570678.318 223963.120, 570684.661 22...

In [46]:
congress_shp['DISTRICT'] = congress_shp['DISTRICT'].apply(lambda x: x.zfill(2))
congress_shp.head()

DISTRICT  POPULATION                                           geometry
0       12      733499  POLYGON ((449362.059 184483.802, 449368.426 18...
1       02      733499  POLYGON ((622633.549 201431.242, 622384.873 20...
2       03      733499  POLYGON ((773148.847 217156.853, 773146.315 21...
3       01      733498  POLYGON ((747975.917 187057.151, 747789.630 18...
4       04      733499  POLYGON ((570678.318 223963.120, 570684.661 22...

In [47]:
cong_precs_split_list = list(cong_split_dictionary.keys())
cong_precs_split = cong_df[cong_df['PREC_CO'].isin(cong_precs_split_list)].copy()
cong_df_dropped  = cong_df[~cong_df['PREC_CO'].isin(cong_precs_split_list)].copy()
display(cong_precs_split)
print(len(cong_precs_split))

PIVOT_COL          PREC_CO  PCON01RBAC  PCON01RGLI  PCON01RNIX  PCON01RSMI  \
455            062_FORSYTH         0.0         0.0         0.0         0.0   
610        096_MECKLENBURG         0.0         0.0         0.0         0.0   
638             10-03_WAKE         0.0         0.0         0.0         0.0   
1102       217_MECKLENBURG         0.0         0.0         0.0         0.0   
1103       218_MECKLENBURG         0.0         0.0         0.0         0.0   
1228            30_CATAWBA         0.0         0.0         0.0         0.0   
1234         30_RUTHERFORD         0.0         0.0         0.0         0.0   
1280            37_CATAWBA         0.0         0.0         0.0         0.0   
2116            KITT_VANCE        18.0        23.0        13.0       106.0   

PIVOT_COL  PCON02DJOH  PCON02DNEL  PCON02DROS  PCON02DTER  PCON04DLOC  \
455               0.0         0.0         0.0         0.0         0.0   
610               0.0         0.0         0.0         0.0         0.0   
638             169.0        15.0       356.0        31.0         1.0   
1102              0.0         0.0         0.0         0.0         0.0   
1103              0.0         0.0         0.0         0.0         0.0   
1228              0.0         0.0         0.0         0.0         0.0   
1234              0.0         0.0         0.0         0.0         0.0   
1280              0.0         0.0         0.0         0.0         0.0   
2116              0.0         0.0         0.0         0.0        22.0   

PIVOT_COL  PCON04DPRI  PCON04RLOO  PCON04RSAR  PCON04RSHA  PCON04RTHO  \
455               0.0         0.0         0.0         0.0         0.0   
610               0.0         0.0         0.0         0.0         0.0   
638               4.0         2.0         2.0         1.0         3.0   
1102              0.0         0.0         0.0         0.0         0.0   
1103              0.0         0.0         0.0         0.0         0.0   
1228              0.0         0.0         0.0         0.0         0.0   
1234              0.0         0.0         0.0         0.0         0.0   
1280              0.0         0.0         0.0         0.0         0.0   
2116            120.0         3.0        11.0         6.0        30.0   

PIVOT_COL  PCON05DBRO  PCON05DHUG  PCON06DDAV  PCON06DFOX  PCON06DHAN  \
455               0.0         0.0         8.0         3.0         2.0   
610               0.0         0.0         0.0         0.0         0.0   
638               0.0         0.0         0.0         0.0         0.0   
1102              0.0         0.0         0.0         0.0         0.0   
1103              0.0         0.0         0.0         0.0         0.0   
1228              3.0         0.0         0.0         0.0         0.0   
1234            163.0        74.0         0.0         0.0         0.0   
1280             14.0         8.0         0.0         0.0         0.0   
2116              0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PCON06DMAN  PCON06DMON  PCON06RHAY  PCON06RPIC  PCON07DCOL  \
455              21.0         0.0        27.0        10.0         0.0   
610               0.0         0.0         0.0         0.0         0.0   
638               0.0         0.0         0.0         0.0         0.0   
1102              0.0         0.0         0.0         0.0         0.0   
1103              0.0         0.0         0.0         0.0         0.0   
1228              0.0         0.0         0.0         0.0         0.0   
1234              0.0         0.0         0.0         0.0         0.0   
1280              0.0         0.0         0.0         0.0         0.0   
2116              0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PCON07DJUD  PCON07DWAR  PCON09DBRO  PCON09DSOU  PCON09DWAL  \
455               0.0         0.0         0.0         0.0         0.0   
610               0.0         0.0         5.0         0.0         1.0   
638               0.0         0.0         0.0         0.0         0.0   
110

9


In [48]:
###ADD DISTRICT COLUMN TO cong_df_dropped
print(len(cong_unsplit_dict))
print(len(cong_df_dropped))
cong_df_dropped['CONG_DIST'] = cong_df_dropped['PREC_CO'].apply(lambda x: cong_unsplit_dict.get(x))
prec_sub = prec[['PREC_ID','ENR_DESC','COUNTY_NAM','COUNTY_ID','MATCH','geometry']]
cong_df_dropped = pd.merge(prec_sub,cong_df_dropped,on='MATCH')
cong_df_dropped.head()

2068
2657


PREC_ID                      ENR_DESC COUNTY_NAM  COUNTY_ID           MATCH  \
0      14           14_Y E SMITH SCHOOL     DURHAM         32       14_DURHAM   
1    EMIS             EMIS_EMERALD ISLE   CARTERET         16   EMIS_CARTERET   
2     131  131_VIENNA ELEMENTARY SCHOOL    FORSYTH         34     131_FORSYTH   
3      MM            MM_MORVEN/MCFARLAN      ANSON          4        MM_ANSON   
4    CRDL                   CRDL_CREDLE  GRANVILLE         39  CRDL_GRANVILLE   

                                            geometry         PREC_CO  \
0  POLYGON ((2043445.004 806092.205, 2043253.389 ...       14_DURHAM   
1  POLYGON ((2566809.355 312013.723, 2567226.337 ...   EMIS_CARTERET   
2  POLYGON ((1580533.350 868933.766, 1580723.583 ...     131_FORSYTH   
3  POLYGON ((1720554.155 385895.605, 1720464.104 ...        MM_ANSON   
4  POLYGON ((2115518.562 932754.945, 2115429.276 ...  CRDL_GRANVILLE   

   PCON01RBAC  PCON01RGLI  PCON01RNIX  PCON01RSMI  PCON02DJOH  PCON02DNEL  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PCON02DROS  PCON02DTER  PCON04DLOC  PCON04DPRI  PCON04RLOO  PCON04RSAR  \
0         0.0         0.0        73.0       493.0         2.0         6.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0        83.0       381.0        12.0        19.0   

   PCON04RSHA  PCON04RTHO  PCON05DBRO  PCON05DHUG  PCON06DDAV  PCON06DFOX  \
0         1.0         3.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         7.0        58.0         0.0         0.0         0.0         0.0   

   PCON06DHAN  PCON06DMAN  PCON06DMON  PCON06RHAY  PCON06RPIC  PCON07DCOL  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PCON07DJUD  PCON07DWAR  PCON09DBRO  PCON09DSOU  PCON09DWAL  PCON09DWIL  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0        19.0       194.0       147.0        24.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PCON10RJOH  PCON10RMCH  PCON10RWAL  PCON11DCOL  PCON11DDAV  PCON11DOSH  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2        85.0       261.0        79.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PCON11DPRI  PCON11DWOO  PCON11RARC  PCON11RBEN  PCON11RBUR  PCON11RCAW  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0

In [49]:
print(len(cong_precs_split))
print(len(cong_split_dictionary))
cong_precs_split_expanded_list = []
for k,v in cong_split_dictionary.items():
    sub_dfs = []
    len_splits = len(v)
    for i in range(0,len_splits):
        dist = v[i]
        sub = cong_precs_split[cong_precs_split['PREC_CO']==k]
        sub['CONG_DIST'] = sub['PREC_CO'].apply(lambda x: dist)
        sub['CONG_DIST'] = sub['CONG_DIST'].astype(str)
        sub['CONG_DIST_long'] = sub['CONG_DIST'].apply(lambda x: ''.join([(' '.join(['[CD-',x])),']']))
        sub['UNIQUE_ID'] = sub.apply(lambda x: ' '.join([x['PREC_CO'],x['CONG_DIST_long']]),axis=1)
        to_keep = []
        for col in sub.columns:
            if col.startswith('PCON'):
                if str(dist) in str(col):
                    to_keep.append(col)
                else:
                    continue
            else:
                to_keep.append(col)
        sub = sub[to_keep]
        sub_dfs.append(sub)
    new_df = pd.concat(sub_dfs)
    cong_precs_split_expanded_list.append(new_df)
cong_precs_split_expanded = pd.concat(cong_precs_split_expanded_list)
cong_precs_split_expanded = cong_precs_split_expanded.fillna(0)
cong_precs_split_expanded_cols = list(cong_precs_split_expanded.columns)
display(cong_precs_split_expanded)

9
9


<ipython-input-49-cb999bdf3f0e>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sub['CONG_DIST'] = sub['PREC_CO'].apply(lambda x: dist)
<ipython-input-49-cb999bdf3f0e>:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sub['CONG_DIST'] = sub['CONG_DIST'].astype(str)
<ipython-input-49-cb999bdf3f0e>:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata

PIVOT_COL          PREC_CO  PCON10RJOH  PCON10RMCH  PCON10RWAL PRECINCT  \
455            062_FORSYTH        55.0       178.0        49.0      062   
455            062_FORSYTH         0.0         0.0         0.0      062   
610        096_MECKLENBURG         0.0         0.0         0.0      096   
610        096_MECKLENBURG         0.0         0.0         0.0      096   
638             10-03_WAKE         0.0         0.0         0.0    10-03   
638             10-03_WAKE         0.0         0.0         0.0    10-03   
1102       217_MECKLENBURG         0.0         0.0         0.0      217   
1102       217_MECKLENBURG         0.0         0.0         0.0      217   
1103       218_MECKLENBURG         0.0         0.0         0.0      218   
1103       218_MECKLENBURG         0.0         0.0         0.0      218   
1228            30_CATAWBA         0.0         0.0         0.0       30   
1228            30_CATAWBA        61.0       460.0        32.0       30   
1234         30_RUTHERFORD         0.0         0.0         0.0       30   
1234         30_RUTHERFORD         0.0         0.0         0.0       30   
1280            37_CATAWBA         0.0         0.0         0.0       37   
1280            37_CATAWBA        42.0       291.0        14.0       37   
2116            KITT_VANCE         0.0         0.0         0.0     KITT   
2116            KITT_VANCE         0.0         0.0         0.0     KITT   

PIVOT_COL       COUNTY            MATCH CONG_DIST CONG_DIST_long  \
455            FORSYTH      062_FORSYTH        10       [CD- 10]   
455            FORSYTH      062_FORSYTH        06       [CD- 06]   
610        MECKLENBURG  096_MECKLENBURG        12       [CD- 12]   
610        MECKLENBURG  096_MECKLENBURG        09       [CD- 09]   
638               WAKE       10-03_WAKE        02       [CD- 02]   
638               WAKE       10-03_WAKE        04       [CD- 04]   
1102       MECKLENBURG  217_MECKLENBURG        12       [CD- 12]   
1102       MECKLENBURG  217_MECKLENBURG        09       [CD- 09]   
1103       MECKLENBURG  218_MECKLENBURG        12       [CD- 12]   
1103       MECKLENBURG  218_MECKLENBURG        09       [CD- 09]   
1228           CATAWBA       30_CATAWBA        05       [CD- 05]   
1228           CATAWBA       30_CATAWBA        10       [CD- 10]   
1234        RUTHERFORD    30_RUTHERFORD        11       [CD- 11]   
1234        RUTHERFORD    30_RUTHERFORD        05       [CD- 05]   
1280           CATAWBA       37_CATAWBA        05       [CD- 05]   
1280           CATAWBA       37_CATAWBA        10       [CD- 10]   
2116             VANCE       KITT_VANCE        04       [CD- 04]   
2116             VANCE       KITT_VANCE        01       [CD- 01]   

PIVOT_COL                 UNIQUE_ID  PCON06DDAV  PCON06DFOX  PCON06DHAN  \
455            062_FORSYTH [CD- 10]         0.0         0.0         0.0   
455            062_FORSYTH [CD- 06]         8.0         3.0         2.0   
610        096_MECKLENBURG [CD- 12]         0.0         0.0         0.0   
610        096_MECKLENBURG [CD- 09]         0.0         0.0         0.0   
638             10-03_WAKE [CD- 02]         0.0         0.0         0.0   
638             10-03_WAKE [CD- 04]         0.0         0.0         0.0   
1102       217_MECKLENBURG [CD- 12]         0.0         0.0         0.0   
1102       217_MECKLENBURG [CD- 09]         0.0         0.0         0.0   
1103       218_MECKLENBURG [CD- 12]         0.0         0.0         0.0   
1103       218_MECKLENBURG [CD- 09]         0.0         0.0         0.0   
1228            30_CATAWBA [CD- 05]         0.0         0.0         0.0   
1228            30_CATAWBA [CD- 10]         0.0         0.0         0.0   
1234         30_RUTHERFORD [CD- 11]         0.0         0.0         0.0   
1234         30_RUTHERFORD [CD- 05]         0.0         0.0         0.0   
1280            37_CATAWBA [CD- 05]         0.0         0.0         0.0   
1280            37_CATAWBA [CD- 10]         0.0         0.0         0.0   
2116  

In [50]:
def make_district_dict(district_shp,district_field):
    keys = []
    values = []
    for i in district_shp[district_field]:
        dist = district_shp[district_shp[district_field]==i].copy()
        dist = dist[[district_field,'geometry']]
        keys.append(i)
        values.append(dist)
    dictionary = dict(zip(keys,values))
    return dictionary

In [51]:
cong_dict = make_district_dict(congress_shp,'DISTRICT')

In [52]:
new_precs = []
for k,v in cong_split_dictionary.items():
    original_geom = prec[prec['MATCH']==k]['geometry']
    original_geom = gp.GeoDataFrame(original_geom)
    original_geom_crs = original_geom.crs
    dists = []
    for i in v:
        dist_of_interest = cong_dict.get(i)
        dists.append(dist_of_interest)
    for i in dists:
        dist_of_interest_geom = i#['geometry']
        district = i['DISTRICT'].unique()[0]
        #print('Current district to split by: ', district)
        dist_of_interest_geom =dist_of_interest_geom.to_crs(original_geom_crs) 
        new_prec = gp.overlay(original_geom, dist_of_interest_geom, how='intersection',keep_geom_type=True)
        new_prec['UNIQUE_ID'] = str(k + ' [CD- '+str(district)+ ']')
        new_precs.append(new_prec)
new_precs = pd.concat(new_precs)
display(new_precs)

cong_precs_split_newgeom = pd.merge(cong_precs_split_expanded,new_precs,on='UNIQUE_ID',how='outer',indicator=True)
cong_precs_split_newgeom['CONG_DIST'] = cong_precs_split_newgeom['DISTRICT']
cong_precs_split_newgeom.drop(columns= ['_merge','DISTRICT'],inplace=True)
display(cong_precs_split_newgeom)

DISTRICT                                           geometry  \
0       10  POLYGON ((1685492.912 873089.856, 1685482.606 ...   
0       06  MULTIPOLYGON (((1684219.341 871034.568, 168421...   
0       12  POLYGON ((1478955.914 506563.835, 1479154.186 ...   
0       09  MULTIPOLYGON (((1475623.100 505867.012, 147560...   
0       02  POLYGON ((2191839.802 733233.584, 2190625.672 ...   
0       04  MULTIPOLYGON (((2200183.732 739173.545, 220022...   
0       12  MULTIPOLYGON (((1492031.497 502849.605, 149207...   
0       09  MULTIPOLYGON (((1476377.649 502498.242, 147639...   
0       12  MULTIPOLYGON (((1492269.646 502564.649, 149226...   
0       09  POLYGON ((1498510.947 498100.838, 1498467.198 ...   
0       05  MULTIPOLYGON (((1326700.300 739772.935, 132664...   
0       10  POLYGON ((1323981.472 737226.179, 1323933.929 ...   
0       11  MULTIPOLYGON (((1124665.590 585508.996, 112464...   
0       05  MULTIPOLYGON (((1134035.605 601179.464, 113401...   
0       05  MULTIPOLYGON (((1307186.772 734864.018, 130718...   
0       10  POLYGON ((1309681.859 734881.153, 1309649.950 ...   
0       04  MULTIPOLYGON (((2181847.112 901266.046, 218184...   
0       01  MULTIPOLYGON (((2144956.855 907183.882, 214501...   

                  UNIQUE_ID  
0      062_FORSYTH [CD- 10]  
0      062_FORSYTH [CD- 06]  
0  096_MECKLENBURG [CD- 12]  
0  096_MECKLENBURG [CD- 09]  
0       10-03_WAKE [CD- 02]  
0       10-03_WAKE [CD- 04]  
0  217_MECKLENBURG [CD- 12]  
0  217_MECKLENBURG [CD- 09]  
0  218_MECKLENBURG [CD- 12]  
0  218_MECKLENBURG [CD- 09]  
0       30_CATAWBA [CD- 05]  
0       30_CATAWBA [CD- 10]  
0    30_RUTHERFORD [CD- 11]  
0    30_RUTHERFORD [CD- 05]  
0       37_CATAWBA [CD- 05]  
0       37_CATAWBA [CD- 10]  
0       KITT_VANCE [CD- 04]  
0       KITT_VANCE [CD- 01]

PREC_CO  PCON10RJOH  PCON10RMCH  PCON10RWAL PRECINCT       COUNTY  \
0       062_FORSYTH        55.0       178.0        49.0      062      FORSYTH   
1       062_FORSYTH         0.0         0.0         0.0      062      FORSYTH   
2   096_MECKLENBURG         0.0         0.0         0.0      096  MECKLENBURG   
3   096_MECKLENBURG         0.0         0.0         0.0      096  MECKLENBURG   
4        10-03_WAKE         0.0         0.0         0.0    10-03         WAKE   
5        10-03_WAKE         0.0         0.0         0.0    10-03         WAKE   
6   217_MECKLENBURG         0.0         0.0         0.0      217  MECKLENBURG   
7   217_MECKLENBURG         0.0         0.0         0.0      217  MECKLENBURG   
8   218_MECKLENBURG         0.0         0.0         0.0      218  MECKLENBURG   
9   218_MECKLENBURG         0.0         0.0         0.0      218  MECKLENBURG   
10       30_CATAWBA         0.0         0.0         0.0       30      CATAWBA   
11       30_CATAWBA        61.0       460.0        32.0       30      CATAWBA   
12    30_RUTHERFORD         0.0         0.0         0.0       30   RUTHERFORD   
13    30_RUTHERFORD         0.0         0.0         0.0       30   RUTHERFORD   
14       37_CATAWBA         0.0         0.0         0.0       37      CATAWBA   
15       37_CATAWBA        42.0       291.0        14.0       37      CATAWBA   
16       KITT_VANCE         0.0         0.0         0.0     KITT        VANCE   
17       KITT_VANCE         0.0         0.0         0.0     KITT        VANCE   

              MATCH CONG_DIST CONG_DIST_long                 UNIQUE_ID  \
0       062_FORSYTH        10       [CD- 10]      062_FORSYTH [CD- 10]   
1       062_FORSYTH        06       [CD- 06]      062_FORSYTH [CD- 06]   
2   096_MECKLENBURG        12       [CD- 12]  096_MECKLENBURG [CD- 12]   
3   096_MECKLENBURG        09       [CD- 09]  096_MECKLENBURG [CD- 09]   
4        10-03_WAKE        02       [CD- 02]       10-03_WAKE [CD- 02]   
5        10-03_WAKE        04       [CD- 04]       10-03_WAKE [CD- 04]   
6   217_MECKLENBURG        12       [CD- 12]  217_MECKLENBURG [CD- 12]   
7   217_MECKLENBURG        09       [CD- 09]  217_MECKLENBURG [CD- 09]   
8   218_MECKLENBURG        12       [CD- 12]  218_MECKLENBURG [CD- 12]   
9   218_MECKLENBURG        09       [CD- 09]  218_MECKLENBURG [CD- 09]   
10       30_CATAWBA        05       [CD- 05]       30_CATAWBA [CD- 05]   
11       30_CATAWBA        10       [CD- 10]       30_CATAWBA [CD- 10]   
12    30_RUTHERFORD        11       [CD- 11]    30_RUTHERFORD [CD- 11]   
13    30_RUTHERFORD        05       [CD- 05]    30_RUTHERFORD [CD- 05]   
14       37_CATAWBA        05       [CD- 05]       37_CATAWBA [CD- 05]   
15       37_CATAWBA        10       [CD- 10]       37_CATAWBA [CD- 10]   
16       KITT_VANCE        04       [CD- 04]       KITT_VANCE [CD- 04]   
17       KITT_VANCE        01       [CD- 01]       KITT_VANCE [CD- 01]   

    PCON06DDAV  PCON06DFOX  PCON06DHAN  PCON06DMAN  PCON06DMON  PCON06RHAY  \
0          0.0         0.0         0.0         0.0         0.0         0.0   
1          8.0         3.0         2.0        21.0         0.0        27.0   
2          0.0         0.0         0.0         0.0         0.0         0.0   
3          0.0         0.0         0.0         0.0         0.0         0.0   
4          0.0         0.0         0.0         0.0         0.0         0.0   
5          0.0         0.0         0.0         0.0         0.0         0.0   
6          0.0         0.0         0.0         0.0         0.0         0.0   
7          0.0         0.0         0.0         0.0         0.0         0.0   
8          0.0         0.0         0.0         0.0         0.0         0.0   
9          0.0         0.0         0.0         0.0         0.0         0.0   
10         0.0         0.0         0.0         0.0         0.0         0.0   
11         0.0         0.0         0.0         0.0         0.0         0.0   
12         0.0         0.0         0.0         0.0 

In [53]:
prec_sub_split_join = prec_sub.drop(columns = ['geometry'])
prec_sub_split_join = pd.DataFrame(prec_sub_split_join)
cong_precs_split_newgeom = pd.merge(cong_precs_split_newgeom,prec_sub_split_join, on = 'MATCH',how='outer',indicator=True)
cong_precs_split_newgeom = cong_precs_split_newgeom[cong_precs_split_newgeom['_merge']=='both']
display(cong_precs_split_newgeom)

PREC_CO  PCON10RJOH  PCON10RMCH  PCON10RWAL PRECINCT       COUNTY  \
0       062_FORSYTH        55.0       178.0        49.0      062      FORSYTH   
1       062_FORSYTH         0.0         0.0         0.0      062      FORSYTH   
2   096_MECKLENBURG         0.0         0.0         0.0      096  MECKLENBURG   
3   096_MECKLENBURG         0.0         0.0         0.0      096  MECKLENBURG   
4        10-03_WAKE         0.0         0.0         0.0    10-03         WAKE   
5        10-03_WAKE         0.0         0.0         0.0    10-03         WAKE   
6   217_MECKLENBURG         0.0         0.0         0.0      217  MECKLENBURG   
7   217_MECKLENBURG         0.0         0.0         0.0      217  MECKLENBURG   
8   218_MECKLENBURG         0.0         0.0         0.0      218  MECKLENBURG   
9   218_MECKLENBURG         0.0         0.0         0.0      218  MECKLENBURG   
10       30_CATAWBA         0.0         0.0         0.0       30      CATAWBA   
11       30_CATAWBA        61.0       460.0        32.0       30      CATAWBA   
12    30_RUTHERFORD         0.0         0.0         0.0       30   RUTHERFORD   
13    30_RUTHERFORD         0.0         0.0         0.0       30   RUTHERFORD   
14       37_CATAWBA         0.0         0.0         0.0       37      CATAWBA   
15       37_CATAWBA        42.0       291.0        14.0       37      CATAWBA   
16       KITT_VANCE         0.0         0.0         0.0     KITT        VANCE   
17       KITT_VANCE         0.0         0.0         0.0     KITT        VANCE   

              MATCH CONG_DIST CONG_DIST_long                 UNIQUE_ID  \
0       062_FORSYTH        10       [CD- 10]      062_FORSYTH [CD- 10]   
1       062_FORSYTH        06       [CD- 06]      062_FORSYTH [CD- 06]   
2   096_MECKLENBURG        12       [CD- 12]  096_MECKLENBURG [CD- 12]   
3   096_MECKLENBURG        09       [CD- 09]  096_MECKLENBURG [CD- 09]   
4        10-03_WAKE        02       [CD- 02]       10-03_WAKE [CD- 02]   
5        10-03_WAKE        04       [CD- 04]       10-03_WAKE [CD- 04]   
6   217_MECKLENBURG        12       [CD- 12]  217_MECKLENBURG [CD- 12]   
7   217_MECKLENBURG        09       [CD- 09]  217_MECKLENBURG [CD- 09]   
8   218_MECKLENBURG        12       [CD- 12]  218_MECKLENBURG [CD- 12]   
9   218_MECKLENBURG        09       [CD- 09]  218_MECKLENBURG [CD- 09]   
10       30_CATAWBA        05       [CD- 05]       30_CATAWBA [CD- 05]   
11       30_CATAWBA        10       [CD- 10]       30_CATAWBA [CD- 10]   
12    30_RUTHERFORD        11       [CD- 11]    30_RUTHERFORD [CD- 11]   
13    30_RUTHERFORD        05       [CD- 05]    30_RUTHERFORD [CD- 05]   
14       37_CATAWBA        05       [CD- 05]       37_CATAWBA [CD- 05]   
15       37_CATAWBA        10       [CD- 10]       37_CATAWBA [CD- 10]   
16       KITT_VANCE        04       [CD- 04]       KITT_VANCE [CD- 04]   
17       KITT_VANCE        01       [CD- 01]       KITT_VANCE [CD- 01]   

    PCON06DDAV  PCON06DFOX  PCON06DHAN  PCON06DMAN  PCON06DMON  PCON06RHAY  \
0          0.0         0.0         0.0         0.0         0.0         0.0   
1          8.0         3.0         2.0        21.0         0.0        27.0   
2          0.0         0.0         0.0         0.0         0.0         0.0   
3          0.0         0.0         0.0         0.0         0.0         0.0   
4          0.0         0.0         0.0         0.0         0.0         0.0   
5          0.0         0.0         0.0         0.0         0.0         0.0   
6          0.0         0.0         0.0         0.0         0.0         0.0   
7          0.0         0.0         0.0         0.0         0.0         0.0   
8          0.0         0.0         0.0         0.0         0.0         0.0   
9          0.0         0.0         0.0         0.0         0.0         0.0   
10         0.0         0.0         0.0         0.0         0.0         0.0   
11         0.0         0.0         0.0         0.0         0.0         0.0   
12         0.0         0.0         0.0         0.0 

In [54]:
##CONCAT THE DFS
cong_final_df = pd.concat([cong_df_dropped,cong_precs_split_newgeom])
for i in cong_final_df.columns:
    if i.startswith('PCON'):
        cong_final_df[i] = cong_final_df[i].fillna(0)
display(cong_final_df.head())
display(cong_final_df.tail())

PREC_ID                      ENR_DESC COUNTY_NAM  COUNTY_ID           MATCH  \
0      14           14_Y E SMITH SCHOOL     DURHAM         32       14_DURHAM   
1    EMIS             EMIS_EMERALD ISLE   CARTERET         16   EMIS_CARTERET   
2     131  131_VIENNA ELEMENTARY SCHOOL    FORSYTH         34     131_FORSYTH   
3      MM            MM_MORVEN/MCFARLAN      ANSON          4        MM_ANSON   
4    CRDL                   CRDL_CREDLE  GRANVILLE         39  CRDL_GRANVILLE   

                                            geometry         PREC_CO  \
0  POLYGON ((2043445.004 806092.205, 2043253.389 ...       14_DURHAM   
1  POLYGON ((2566809.355 312013.723, 2567226.337 ...   EMIS_CARTERET   
2  POLYGON ((1580533.350 868933.766, 1580723.583 ...     131_FORSYTH   
3  POLYGON ((1720554.155 385895.605, 1720464.104 ...        MM_ANSON   
4  POLYGON ((2115518.562 932754.945, 2115429.276 ...  CRDL_GRANVILLE   

   PCON01RBAC  PCON01RGLI  PCON01RNIX  PCON01RSMI  PCON02DJOH  PCON02DNEL  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PCON02DROS  PCON02DTER  PCON04DLOC  PCON04DPRI  PCON04RLOO  PCON04RSAR  \
0         0.0         0.0        73.0       493.0         2.0         6.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0        83.0       381.0        12.0        19.0   

   PCON04RSHA  PCON04RTHO  PCON05DBRO  PCON05DHUG  PCON06DDAV  PCON06DFOX  \
0         1.0         3.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         7.0        58.0         0.0         0.0         0.0         0.0   

   PCON06DHAN  PCON06DMAN  PCON06DMON  PCON06RHAY  PCON06RPIC  PCON07DCOL  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PCON07DJUD  PCON07DWAR  PCON09DBRO  PCON09DSOU  PCON09DWAL  PCON09DWIL  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0        19.0       194.0       147.0        24.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PCON10RJOH  PCON10RMCH  PCON10RWAL  PCON11DCOL  PCON11DDAV  PCON11DOSH  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2        85.0       261.0        79.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PCON11DPRI  PCON11DWOO  PCON11RARC  PCON11RBEN  PCON11RBUR  PCON11RCAW  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0

PREC_ID        ENR_DESC  COUNTY_NAM  COUNTY_ID          MATCH  \
13      30     30_SPINDALE  RUTHERFORD         81  30_RUTHERFORD   
14      37  37_VIEWMONT #2     CATAWBA         18     37_CATAWBA   
15      37  37_VIEWMONT #2     CATAWBA         18     37_CATAWBA   
16    KITT            KITT       VANCE         91     KITT_VANCE   
17    KITT            KITT       VANCE         91     KITT_VANCE   

                                             geometry        PREC_CO  \
13  MULTIPOLYGON (((1134035.605 601179.464, 113401...  30_RUTHERFORD   
14  MULTIPOLYGON (((1307186.772 734864.018, 130718...     37_CATAWBA   
15  POLYGON ((1309681.859 734881.153, 1309649.950 ...     37_CATAWBA   
16  MULTIPOLYGON (((2181847.112 901266.046, 218184...     KITT_VANCE   
17  MULTIPOLYGON (((2144956.855 907183.882, 214501...     KITT_VANCE   

    PCON01RBAC  PCON01RGLI  PCON01RNIX  PCON01RSMI  PCON02DJOH  PCON02DNEL  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0         0.0         0.0         0.0         0.0   
17        18.0        23.0        13.0       106.0         0.0         0.0   

    PCON02DROS  PCON02DTER  PCON04DLOC  PCON04DPRI  PCON04RLOO  PCON04RSAR  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0        22.0       120.0         3.0        11.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PCON04RSHA  PCON04RTHO  PCON05DBRO  PCON05DHUG  PCON06DDAV  PCON06DFOX  \
13         0.0         0.0       163.0        74.0         0.0         0.0   
14         0.0         0.0        14.0         8.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         6.0        30.0         0.0         0.0         0.0         0.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PCON06DHAN  PCON06DMAN  PCON06DMON  PCON06RHAY  PCON06RPIC  PCON07DCOL  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0         0.0         0.0         0.0         0.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PCON07DJUD  PCON07DWAR  PCON09DBRO  PCON09DSOU  PCON09DWAL  PCON09DWIL  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0         0.0         0.0         0.0         0.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PCON10RJOH  PCON10RMCH  PCON10RWAL  PCON11DCOL  PCON11DDAV  PCON11DOSH  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15        42.0       291.0        14.0         0.0         0.0         0.0   
16         0.0         0.0         0.0         0.0         0.0         0.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PCON11DPRI  PCON11DWOO  PCON11RARC  PCON11RBEN  PCON11RBUR  PCON11RCAW  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0         

In [55]:
congress_shp['CONG_DIST'] = congress_shp['DISTRICT'].astype(str)

In [56]:
cong_final_df['COUNTY_ID'] = cong_final_df['COUNTY_ID'].astype(str)
cong_final_df['COUNTYFP'] = cong_final_df['COUNTY_ID'].apply(lambda x: str(x).zfill(3))
cong_final_df['UNIQUE_ID'] = cong_final_df['UNIQUE_ID'].astype(str)
cong_final_df['UNIQUE_ID'] = cong_final_df.apply(lambda x: x['MATCH'] if x['UNIQUE_ID']=='nan' else x['UNIQUE_ID'],axis=1)
cong_final_df.drop(columns = ['PREC_CO','MATCH','PRECINCT','COUNTY','CONG_DIST_long','_merge'],inplace=True)
cong_final_df_cols = list(cong_final_df.columns)
cong_final_df_cols.remove('geometry')
cong_final_df_cols.remove('CONG_DIST')
cong_final_df_cols.remove('UNIQUE_ID')
cong_final_df_cols.remove('COUNTYFP')
cong_final_df_cols[0:1] = ['UNIQUE_ID','COUNTYFP']
cong_final_df_cols[5:5] = ['CONG_DIST']
cong_final_df_cols.append('geometry')
cong_final_df = cong_final_df[cong_final_df_cols]
cong_final_df['CONG_DIST'] = cong_final_df['CONG_DIST'].astype(str)
cong_final_df['CONG_DIST'] = cong_final_df['CONG_DIST'].apply(lambda x: "n/a" if x in [0,'0','None','nan',np.nan] else x)

for i in cong_final_df.columns:
    if i.startswith('P'):
        try:
            cong_final_df[i] = cong_final_df[i].astype(int)
        except:
            print('Could not convert: ', i)
            for value in cong_final_df[i].unique():
                print(value)
    elif i!='geometry':
        cong_final_df[i]= cong_final_df[i].astype(str)
    else:
        continue
display(cong_final_df.head())
display(cong_final_df.tail())

UNIQUE_ID COUNTYFP                      ENR_DESC COUNTY_NAM COUNTY_ID  \
0       14_DURHAM      032           14_Y E SMITH SCHOOL     DURHAM        32   
1   EMIS_CARTERET      016             EMIS_EMERALD ISLE   CARTERET        16   
2     131_FORSYTH      034  131_VIENNA ELEMENTARY SCHOOL    FORSYTH        34   
3        MM_ANSON      004            MM_MORVEN/MCFARLAN      ANSON         4   
4  CRDL_GRANVILLE      039                   CRDL_CREDLE  GRANVILLE        39   

  CONG_DIST  PCON01RBAC  PCON01RGLI  PCON01RNIX  PCON01RSMI  PCON02DJOH  \
0        04           0           0           0           0           0   
1       n/a           0           0           0           0           0   
2        10           0           0           0           0           0   
3        09           0           0           0           0           0   
4        04           0           0           0           0           0   

   PCON02DNEL  PCON02DROS  PCON02DTER  PCON04DLOC  PCON04DPRI  PCON04RLOO  \
0           0           0           0          73         493           2   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0          83         381          12   

   PCON04RSAR  PCON04RSHA  PCON04RTHO  PCON05DBRO  PCON05DHUG  PCON06DDAV  \
0           6           1           3           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4          19           7          58           0           0           0   

   PCON06DFOX  PCON06DHAN  PCON06DMAN  PCON06DMON  PCON06RHAY  PCON06RPIC  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   PCON07DCOL  PCON07DJUD  PCON07DWAR  PCON09DBRO  PCON09DSOU  PCON09DWAL  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0          19         194         147   
4           0           0           0           0           0           0   

   PCON09DWIL  PCON10RJOH  PCON10RMCH  PCON10RWAL  PCON11DCOL  PCON11DDAV  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0          85         261          79           0           0   
3          24           0           0           0           0           0   
4           0           0           0           0           0           0   

   PCON11DOSH  PCON11DPRI  PCON11DWOO  PCON11RARC  PCON11RBEN  PCON11RBUR  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   PCON11RCAW  PCON11RDAV  PCON11RDRI  PCON11RFEK  PCON11RGEN  PCON11RKIN  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0

UNIQUE_ID COUNTYFP        ENR_DESC  COUNTY_NAM COUNTY_ID  \
13  30_RUTHERFORD [CD- 05]      081     30_SPINDALE  RUTHERFORD        81   
14     37_CATAWBA [CD- 05]      018  37_VIEWMONT #2     CATAWBA        18   
15     37_CATAWBA [CD- 10]      018  37_VIEWMONT #2     CATAWBA        18   
16     KITT_VANCE [CD- 04]      091            KITT       VANCE        91   
17     KITT_VANCE [CD- 01]      091            KITT       VANCE        91   

   CONG_DIST  PCON01RBAC  PCON01RGLI  PCON01RNIX  PCON01RSMI  PCON02DJOH  \
13        05           0           0           0           0           0   
14        05           0           0           0           0           0   
15        10           0           0           0           0           0   
16        04           0           0           0           0           0   
17        01          18          23          13         106           0   

    PCON02DNEL  PCON02DROS  PCON02DTER  PCON04DLOC  PCON04DPRI  PCON04RLOO  \
13           0           0           0           0           0           0   
14           0           0           0           0           0           0   
15           0           0           0           0           0           0   
16           0           0           0          22         120           3   
17           0           0           0           0           0           0   

    PCON04RSAR  PCON04RSHA  PCON04RTHO  PCON05DBRO  PCON05DHUG  PCON06DDAV  \
13           0           0           0         163          74           0   
14           0           0           0          14           8           0   
15           0           0           0           0           0           0   
16          11           6          30           0           0           0   
17           0           0           0           0           0           0   

    PCON06DFOX  PCON06DHAN  PCON06DMAN  PCON06DMON  PCON06RHAY  PCON06RPIC  \
13           0           0           0           0           0           0   
14           0           0           0           0           0           0   
15           0           0           0           0           0           0   
16           0           0           0           0           0           0   
17           0           0           0           0           0           0   

    PCON07DCOL  PCON07DJUD  PCON07DWAR  PCON09DBRO  PCON09DSOU  PCON09DWAL  \
13           0           0           0           0           0           0   
14           0           0           0           0           0           0   
15           0           0           0           0           0           0   
16           0           0           0           0           0           0   
17           0           0           0           0           0           0   

    PCON09DWIL  PCON10RJOH  PCON10RMCH  PCON10RWAL  PCON11DCOL  PCON11DDAV  \
13           0           0           0           0           0           0   
14           0           0           0           0           0           0   
15           0          42         291          14           0           0   
16           0           0           0           0           0           0   
17           0           0           0           0           0           0   

    PCON11DOSH  PCON11DPRI  PCON11DWOO  PCON11RARC  PCON11RBEN  PCON11RBUR  \
13           0           0           0           0           0           0   
14           0           0           0           0           0           0   
15           0           0           0           0           0           0   
16           0           0           0           0           0           0   
17           0           0           0           0           0           0   

    PCON11RCAW  PCON11RDAV  PCON11RDRI  PCON11RFEK  PCON11RGEN  PCON11RKIN  \
13           0           0           0           0           0           0   
14           0           0           0           0           0           0   
15           0           0           0           

In [57]:
cong_final_df.to_file('./nc_prim_20_cong_prec.shp')

### Process House of Representatives dataframe

In [58]:
### READ IN THE HOR FILE
districts = os.path.join(source_files, 'district_bounds')
house_folder = os.path.join(districts,'state_house')
house_shp = gp.read_file(os.path.join(house_folder,'HB 1020 H Red Comm CSBK-25.shp'))
house_shp.head()

DISTRICT                                           geometry
0        1  POLYGON ((850157.570 313952.432, 850174.392 31...
1       10  POLYGON ((700251.524 185408.186, 700232.723 18...
2      109  POLYGON ((402901.840 158912.067, 402916.417 15...
3      110  POLYGON ((416839.438 185947.087, 416909.408 18...
4       83  POLYGON ((453343.349 180266.149, 453459.859 18...

In [59]:
house_shp['DISTRICT'] = house_shp['DISTRICT'].apply(lambda x: x.zfill(3))
house_shp.head()

DISTRICT                                           geometry
0      001  POLYGON ((850157.570 313952.432, 850174.392 31...
1      010  POLYGON ((700251.524 185408.186, 700232.723 18...
2      109  POLYGON ((402901.840 158912.067, 402916.417 15...
3      110  POLYGON ((416839.438 185947.087, 416909.408 18...
4      083  POLYGON ((453343.349 180266.149, 453459.859 18...

In [60]:
sldl_precs_split_list = list(sldl_split_dictionary.keys())
sldl_precs_split = sldl_df[sldl_df['PREC_CO'].isin(sldl_precs_split_list)].copy()
sldl_df_dropped  = sldl_df[~sldl_df['PREC_CO'].isin(sldl_precs_split_list)].copy()
display(sldl_precs_split)
print(len(sldl_precs_split))

PIVOT_COL          PREC_CO  PSL003RKOH  PSL003RQUE  PSL003RSMI  PSL003RTYS  \
751         12-13_CABARRUS         0.0         0.0         0.0         0.0   
891             15-01_WAKE         0.0         0.0         0.0         0.0   
892             15-02_WAKE         0.0         0.0         0.0         0.0   
916             1513B_PITT         0.0         0.0         0.0         0.0   
1540       AH49_CUMBERLAND         0.0         0.0         0.0         0.0   
1665       CC31_CUMBERLAND         0.0         0.0         0.0         0.0   
1718          CLEA_SAMPSON         0.0         0.0         0.0         0.0   
1744       CU02_CUMBERLAND         0.0         0.0         0.0         0.0   
1959        G8A_CUMBERLAND         0.0         0.0         0.0         0.0   

PIVOT_COL  PSL005DHUN  PSL005DRIV  PSL006RHAN  PSL006RROL  PSL009DFAR  \
751               0.0         0.0         0.0         0.0         0.0   
891               0.0         0.0         0.0         0.0         0.0   
892               0.0         0.0         0.0         0.0         0.0   
916               0.0         0.0         0.0         0.0        58.0   
1540              0.0         0.0         0.0         0.0         0.0   
1665              0.0         0.0         0.0         0.0         0.0   
1718              0.0         0.0         0.0         0.0         0.0   
1744              0.0         0.0         0.0         0.0         0.0   
1959              0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PSL009DHOC  PSL012DBRE  PSL012DBRO  PSL012DCOX  PSL014RCLE  \
751               0.0         0.0         0.0         0.0         0.0   
891               0.0         0.0         0.0         0.0         0.0   
892               0.0         0.0         0.0         0.0         0.0   
916              50.0        53.0        54.0       186.0         0.0   
1540              0.0         0.0         0.0         0.0         0.0   
1665              0.0         0.0         0.0         0.0         0.0   
1718              0.0         0.0         0.0         0.0         0.0   
1744              0.0         0.0         0.0         0.0         0.0   
1959              0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PSL014REDW  PSL015RPRI  PSL015RSHE  PSL019DDAW  PSL019DMOR  \
751               0.0         0.0         0.0         0.0         0.0   
891               0.0         0.0         0.0         0.0         0.0   
892               0.0         0.0         0.0         0.0         0.0   
916               0.0         0.0         0.0         0.0         0.0   
1540              0.0         0.0         0.0         0.0         0.0   
1665              0.0         0.0         0.0         0.0         0.0   
1718              0.0         0.0         0.0         0.0         0.0   
1744              0.0         0.0         0.0         0.0         0.0   
1959              0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PSL019RMIL  PSL019RPER  PSL020RDAV  PSL020RLAN  PSL021DPEA  \
751               0.0         0.0         0.0         0.0         0.0   
891               0.0         0.0         0.0         0.0         0.0   
892               0.0         0.0         0.0         0.0         0.0   
916               0.0         0.0         0.0         0.0         0.0   
1540              0.0         0.0         0.0         0.0         0.0   
1665              0.0         0.0         0.0         0.0         0.0   
1718              0.0         0.0         0.0         0.0       158.0   
1744              0.0         0.0         0.0         0.0         0.0   
1959              0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  PSL021DSMI  PSL022DDEN  PSL022DKIR  PSL024DFAR  PSL024DMCN  \
751               0.0         0.0         0.0         0.0         0.0   
891               0.0         0.0         0.0         0.0         0.0   
892               0.0         0.0         0.0         0.0         0.0   
916

9


In [61]:
###ADD DISTRICT COLUMN TO sldl_df_dropped
print(len(sldl_unsplit_dict))
print(len(sldl_df_dropped))
sldl_df_dropped['SLDL_DIST'] = sldl_df_dropped['PREC_CO'].apply(lambda x: sldl_unsplit_dict.get(x))
prec_sub = prec[['PREC_ID','ENR_DESC','COUNTY_NAM','COUNTY_ID','MATCH','geometry']]
sldl_df_dropped = pd.merge(prec_sub,sldl_df_dropped,on='MATCH')
sldl_df_dropped.head()

884
2657


PREC_ID                      ENR_DESC COUNTY_NAM  COUNTY_ID           MATCH  \
0      14           14_Y E SMITH SCHOOL     DURHAM         32       14_DURHAM   
1    EMIS             EMIS_EMERALD ISLE   CARTERET         16   EMIS_CARTERET   
2     131  131_VIENNA ELEMENTARY SCHOOL    FORSYTH         34     131_FORSYTH   
3      MM            MM_MORVEN/MCFARLAN      ANSON          4        MM_ANSON   
4    CRDL                   CRDL_CREDLE  GRANVILLE         39  CRDL_GRANVILLE   

                                            geometry         PREC_CO  \
0  POLYGON ((2043445.004 806092.205, 2043253.389 ...       14_DURHAM   
1  POLYGON ((2566809.355 312013.723, 2567226.337 ...   EMIS_CARTERET   
2  POLYGON ((1580533.350 868933.766, 1580723.583 ...     131_FORSYTH   
3  POLYGON ((1720554.155 385895.605, 1720464.104 ...        MM_ANSON   
4  POLYGON ((2115518.562 932754.945, 2115429.276 ...  CRDL_GRANVILLE   

   PSL003RKOH  PSL003RQUE  PSL003RSMI  PSL003RTYS  PSL005DHUN  PSL005DRIV  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL006RHAN  PSL006RROL  PSL009DFAR  PSL009DHOC  PSL012DBRE  PSL012DBRO  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL012DCOX  PSL014RCLE  PSL014REDW  PSL015RPRI  PSL015RSHE  PSL019DDAW  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL019DMOR  PSL019RMIL  PSL019RPER  PSL020RDAV  PSL020RLAN  PSL021DPEA  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL021DSMI  PSL022DDEN  PSL022DKIR  PSL024DFAR  PSL024DMCN  PSL025RCHE  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL025RMAT  PSL026RTAT  PSL026RWHI  PSL027DHIC  PSL027DMCD  PSL027DWRA  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL033DGIL  PSL033DMAR  PSL035RCAN  PSL035RPET  PSL036RCOL  PSL036RPAG  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0

In [62]:
print(len(sldl_precs_split))
print(len(sldl_split_dictionary))
sldl_precs_split_expanded_list = []
for k,v in sldl_split_dictionary.items():
    sub_dfs = []
    len_splits = len(v)
    for i in range(0,len_splits):
        dist = v[i]
        sub = sldl_precs_split[sldl_precs_split['PREC_CO']==k]
        sub['SLDL_DIST'] = sub['PREC_CO'].apply(lambda x: dist)
        sub['SLDL_DIST'] = sub['SLDL_DIST'].astype(str)
        sub['SLDL_DIST_long'] = sub['SLDL_DIST'].apply(lambda x: ''.join([(' '.join(['[SLDL -',x])),']']))
        sub['UNIQUE_ID'] = sub.apply(lambda x: ' '.join([x['PREC_CO'],x['SLDL_DIST_long']]),axis=1)
        to_keep = []
        for col in sub.columns:
            if col.startswith('PSL'):
                if str(dist) in str(col):
                    to_keep.append(col)
                else:
                    continue
            else:
                to_keep.append(col)
        sub = sub[to_keep]
        sub_dfs.append(sub)
    new_df = pd.concat(sub_dfs)
    sldl_precs_split_expanded_list.append(new_df)
sldl_precs_split_expanded = pd.concat(sldl_precs_split_expanded_list)
sldl_precs_split_expanded = sldl_precs_split_expanded.fillna(0)
sldl_precs_split_expanded_cols = list(sldl_precs_split_expanded.columns)
display(sldl_precs_split_expanded)

9
9


<ipython-input-62-ef34b33adf6d>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sub['SLDL_DIST'] = sub['PREC_CO'].apply(lambda x: dist)
<ipython-input-62-ef34b33adf6d>:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sub['SLDL_DIST'] = sub['SLDL_DIST'].astype(str)
<ipython-input-62-ef34b33adf6d>:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata

PIVOT_COL          PREC_CO  PSL082DPIL  PSL082DSTE  PSL082RBAK  PSL082RHAM  \
751         12-13_CABARRUS        85.0       335.0        90.0        71.0   
751         12-13_CABARRUS         0.0         0.0         0.0         0.0   
891             15-01_WAKE         0.0         0.0         0.0         0.0   
891             15-01_WAKE         0.0         0.0         0.0         0.0   
892             15-02_WAKE         0.0         0.0         0.0         0.0   
892             15-02_WAKE         0.0         0.0         0.0         0.0   
916             1513B_PITT         0.0         0.0         0.0         0.0   
916             1513B_PITT         0.0         0.0         0.0         0.0   
1540       AH49_CUMBERLAND         0.0         0.0         0.0         0.0   
1540       AH49_CUMBERLAND         0.0         0.0         0.0         0.0   
1665       CC31_CUMBERLAND         0.0         0.0         0.0         0.0   
1665       CC31_CUMBERLAND         0.0         0.0         0.0         0.0   
1718          CLEA_SAMPSON         0.0         0.0         0.0         0.0   
1718          CLEA_SAMPSON         0.0         0.0         0.0         0.0   
1744       CU02_CUMBERLAND         0.0         0.0         0.0         0.0   
1744       CU02_CUMBERLAND         0.0         0.0         0.0         0.0   
1959        G8A_CUMBERLAND         0.0         0.0         0.0         0.0   
1959        G8A_CUMBERLAND         0.0         0.0         0.0         0.0   

PIVOT_COL  PSL082RMOF PRECINCT      COUNTY            MATCH SLDL_DIST  \
751              22.0    12-13    CABARRUS   12-13_CABARRUS       082   
751               0.0    12-13    CABARRUS   12-13_CABARRUS       083   
891               0.0    15-01        WAKE       15-01_WAKE       033   
891               0.0    15-01        WAKE       15-01_WAKE       037   
892               0.0    15-02        WAKE       15-02_WAKE       033   
892               0.0    15-02        WAKE       15-02_WAKE       036   
916               0.0    1513B        PITT       1513B_PITT       009   
916               0.0    1513B        PITT       1513B_PITT       012   
1540              0.0     AH49  CUMBERLAND  AH49_CUMBERLAND       044   
1540              0.0     AH49  CUMBERLAND  AH49_CUMBERLAND       045   
1665              0.0     CC31  CUMBERLAND  CC31_CUMBERLAND       044   
1665              0.0     CC31  CUMBERLAND  CC31_CUMBERLAND       045   
1718              0.0     CLEA     SAMPSON     CLEA_SAMPSON       022   
1718              0.0     CLEA     SAMPSON     CLEA_SAMPSON       021   
1744              0.0     CU02  CUMBERLAND  CU02_CUMBERLAND       044   
1744              0.0     CU02  CUMBERLAND  CU02_CUMBERLAND       045   
1959              0.0      G8A  CUMBERLAND   G8A_CUMBERLAND       044   
1959              0.0      G8A  CUMBERLAND   G8A_CUMBERLAND       045   

PIVOT_COL SLDL_DIST_long                     UNIQUE_ID  PSL083RPIT  \
751         [SLDL - 082]   12-13_CABARRUS [SLDL - 082]         0.0   
751         [SLDL - 083]   12-13_CABARRUS [SLDL - 083]        15.0   
891         [SLDL - 033]       15-01_WAKE [SLDL - 033]         0.0   
891         [SLDL - 037]       15-01_WAKE [SLDL - 037]         0.0   
892         [SLDL - 033]       15-02_WAKE [SLDL - 033]         0.0   
892         [SLDL - 036]       15-02_WAKE [SLDL - 036]         0.0   
916         [SLDL - 009]       1513B_PITT [SLDL - 009]         0.0   
916         [SLDL - 012]       1513B_PITT [SLDL - 012]         0.0   
1540        [SLDL - 044]  AH49_CUMBERLAND [SLDL - 044]         0.0   
1540        [SLDL - 045]  AH49_CUMBERLAND [SLDL - 045]         0.0   
1665        [SLDL - 044]  CC31_CUMBERLAND [SLDL - 044]         0.0   
1665        [SLDL - 045]  CC31_CUMBERLAND [SLDL - 045]         0.0   
1718        [SLDL - 022]     CLEA_SAMPSON [SLDL - 022]         0.0   
1718        [SLDL - 021]     CLEA_SAMPSON [SLDL - 021]         0.0   
1744        [SLDL - 044]  CU02_CUMBERLAND [SLDL - 044]         0.0   
1744     

In [63]:
sldl_dict = make_district_dict(house_shp,'DISTRICT')

In [64]:
new_precs = []
for k,v in sldl_split_dictionary.items():
    original_geom = prec[prec['MATCH']==k]['geometry']
    original_geom = gp.GeoDataFrame(original_geom)
    original_geom_crs = original_geom.crs
    dists = []
    for i in v:
        dist_of_interest = sldl_dict.get(i)
        dists.append(dist_of_interest)
    for i in dists:
        dist_of_interest_geom = i#['geometry']
        district = i['DISTRICT'].unique()[0]
        #print('Current district to split by: ', district)
        dist_of_interest_geom =dist_of_interest_geom.to_crs(original_geom_crs) 
        new_prec = gp.overlay(original_geom, dist_of_interest_geom, how='intersection',keep_geom_type=True)
        new_prec['UNIQUE_ID'] = str(k + ' [SLDL - '+str(district)+ ']')
        new_precs.append(new_prec)
new_precs = pd.concat(new_precs)
display(new_precs)

sldl_precs_split_newgeom = pd.merge(sldl_precs_split_expanded,new_precs,on='UNIQUE_ID',how='outer',indicator=True)
sldl_precs_split_newgeom['SLDL_DIST'] = sldl_precs_split_newgeom['DISTRICT']
sldl_precs_split_newgeom.drop(columns= ['_merge','DISTRICT'],inplace=True)
display(sldl_precs_split_newgeom)

DISTRICT                                           geometry  \
0      082  POLYGON ((1525796.910 604849.735, 1525687.571 ...   
0      083  MULTIPOLYGON (((1529118.728 601523.771, 152908...   
0      033  MULTIPOLYGON (((2108109.413 679129.824, 210808...   
0      037  POLYGON ((2116263.255 672155.355, 2115734.269 ...   
0      033  MULTIPOLYGON (((2099152.954 693736.533, 209912...   
0      036  POLYGON ((2095146.296 681971.898, 2095030.243 ...   
0      009  MULTIPOLYGON (((2489934.081 637922.218, 248993...   
0      012  POLYGON ((2489933.883 638059.812, 2489961.179 ...   
0      044  POLYGON ((2007593.933 459328.488, 2007526.858 ...   
0      045  MULTIPOLYGON (((2006280.243 458935.864, 200580...   
0      044  MULTIPOLYGON (((2008596.888 463837.919, 200865...   
0      045  MULTIPOLYGON (((2008641.878 464119.548, 200863...   
0      022  MULTIPOLYGON (((2231043.118 446301.609, 223105...   
0      021  POLYGON ((2202564.917 473728.992, 2202564.917 ...   
0      044  MULTIPOLYGON (((2008221.765 459424.047, 200822...   
0      045  POLYGON ((2014492.174 462676.707, 2014629.679 ...   
0      044  MULTIPOLYGON (((2005162.814 458262.364, 200516...   
0      045  POLYGON ((2002759.204 455744.707, 2002369.596 ...   

                      UNIQUE_ID  
0   12-13_CABARRUS [SLDL - 082]  
0   12-13_CABARRUS [SLDL - 083]  
0       15-01_WAKE [SLDL - 033]  
0       15-01_WAKE [SLDL - 037]  
0       15-02_WAKE [SLDL - 033]  
0       15-02_WAKE [SLDL - 036]  
0       1513B_PITT [SLDL - 009]  
0       1513B_PITT [SLDL - 012]  
0  AH49_CUMBERLAND [SLDL - 044]  
0  AH49_CUMBERLAND [SLDL - 045]  
0  CC31_CUMBERLAND [SLDL - 044]  
0  CC31_CUMBERLAND [SLDL - 045]  
0     CLEA_SAMPSON [SLDL - 022]  
0     CLEA_SAMPSON [SLDL - 021]  
0  CU02_CUMBERLAND [SLDL - 044]  
0  CU02_CUMBERLAND [SLDL - 045]  
0   G8A_CUMBERLAND [SLDL - 044]  
0   G8A_CUMBERLAND [SLDL - 045]

PREC_CO  PSL082DPIL  PSL082DSTE  PSL082RBAK  PSL082RHAM  \
0    12-13_CABARRUS        85.0       335.0        90.0        71.0   
1    12-13_CABARRUS         0.0         0.0         0.0         0.0   
2        15-01_WAKE         0.0         0.0         0.0         0.0   
3        15-01_WAKE         0.0         0.0         0.0         0.0   
4        15-02_WAKE         0.0         0.0         0.0         0.0   
5        15-02_WAKE         0.0         0.0         0.0         0.0   
6        1513B_PITT         0.0         0.0         0.0         0.0   
7        1513B_PITT         0.0         0.0         0.0         0.0   
8   AH49_CUMBERLAND         0.0         0.0         0.0         0.0   
9   AH49_CUMBERLAND         0.0         0.0         0.0         0.0   
10  CC31_CUMBERLAND         0.0         0.0         0.0         0.0   
11  CC31_CUMBERLAND         0.0         0.0         0.0         0.0   
12     CLEA_SAMPSON         0.0         0.0         0.0         0.0   
13     CLEA_SAMPSON         0.0         0.0         0.0         0.0   
14  CU02_CUMBERLAND         0.0         0.0         0.0         0.0   
15  CU02_CUMBERLAND         0.0         0.0         0.0         0.0   
16   G8A_CUMBERLAND         0.0         0.0         0.0         0.0   
17   G8A_CUMBERLAND         0.0         0.0         0.0         0.0   

    PSL082RMOF PRECINCT      COUNTY            MATCH SLDL_DIST SLDL_DIST_long  \
0         22.0    12-13    CABARRUS   12-13_CABARRUS       082   [SLDL - 082]   
1          0.0    12-13    CABARRUS   12-13_CABARRUS       083   [SLDL - 083]   
2          0.0    15-01        WAKE       15-01_WAKE       033   [SLDL - 033]   
3          0.0    15-01        WAKE       15-01_WAKE       037   [SLDL - 037]   
4          0.0    15-02        WAKE       15-02_WAKE       033   [SLDL - 033]   
5          0.0    15-02        WAKE       15-02_WAKE       036   [SLDL - 036]   
6          0.0    1513B        PITT       1513B_PITT       009   [SLDL - 009]   
7          0.0    1513B        PITT       1513B_PITT       012   [SLDL - 012]   
8          0.0     AH49  CUMBERLAND  AH49_CUMBERLAND       044   [SLDL - 044]   
9          0.0     AH49  CUMBERLAND  AH49_CUMBERLAND       045   [SLDL - 045]   
10         0.0     CC31  CUMBERLAND  CC31_CUMBERLAND       044   [SLDL - 044]   
11         0.0     CC31  CUMBERLAND  CC31_CUMBERLAND       045   [SLDL - 045]   
12         0.0     CLEA     SAMPSON     CLEA_SAMPSON       022   [SLDL - 022]   
13         0.0     CLEA     SAMPSON     CLEA_SAMPSON       021   [SLDL - 021]   
14         0.0     CU02  CUMBERLAND  CU02_CUMBERLAND       044   [SLDL - 044]   
15         0.0     CU02  CUMBERLAND  CU02_CUMBERLAND       045   [SLDL - 045]   
16         0.0      G8A  CUMBERLAND   G8A_CUMBERLAND       044   [SLDL - 044]   
17         0.0      G8A  CUMBERLAND   G8A_CUMBERLAND       045   [SLDL - 045]   

                       UNIQUE_ID  PSL083RPIT  PSL083RWHI  PSL033DGIL  \
0    12-13_CABARRUS [SLDL - 082]         0.0         0.0         0.0   
1    12-13_CABARRUS [SLDL - 083]        15.0        12.0         0.0   
2        15-01_WAKE [SLDL - 033]         0.0         0.0        88.0   
3        15-01_WAKE [SLDL - 037]         0.0         0.0         0.0   
4        15-02_WAKE [SLDL - 033]         0.0         0.0       273.0   
5        15-02_WAKE [SLDL - 036]         0.0         0.0         0.0   
6        1513B_PITT [SLDL - 009]         0.0         0.0         0.0   
7        1513B_PITT [SLDL - 012]         0.0         0.0         0.0   
8   AH49_CUMBERLAND [SLDL - 044]         0.0         0.0         0.0   
9   AH49_CUMBERLAND [SLDL - 045]         0.0         0.0         0.0   
10  CC31_CUMBERLAND [SLDL - 044]         0.0         0.0         0.0   
11  CC31_CUMBERLAND [SLDL - 045]         0.0         0.0         0.0   
12     CLEA_SAMPSON [SLDL - 022]         0.0         0.0         0.0   
13     CLEA_SAMPSON [SLDL - 021]         0.0         0.0         0.0   
14  CU02_CUMBERLAND [SLDL - 044]         0

In [65]:
sldl_precs_split_newgeom = pd.merge(sldl_precs_split_newgeom,prec_sub_split_join,on='MATCH', how = 'outer',indicator = True)
sldl_precs_split_newgeom = sldl_precs_split_newgeom[sldl_precs_split_newgeom['_merge']=='both']
sldl_precs_split_newgeom.drop(columns=['_merge'],inplace=True)
display(sldl_precs_split_newgeom)

PREC_CO  PSL082DPIL  PSL082DSTE  PSL082RBAK  PSL082RHAM  \
0    12-13_CABARRUS        85.0       335.0        90.0        71.0   
1    12-13_CABARRUS         0.0         0.0         0.0         0.0   
2        15-01_WAKE         0.0         0.0         0.0         0.0   
3        15-01_WAKE         0.0         0.0         0.0         0.0   
4        15-02_WAKE         0.0         0.0         0.0         0.0   
5        15-02_WAKE         0.0         0.0         0.0         0.0   
6        1513B_PITT         0.0         0.0         0.0         0.0   
7        1513B_PITT         0.0         0.0         0.0         0.0   
8   AH49_CUMBERLAND         0.0         0.0         0.0         0.0   
9   AH49_CUMBERLAND         0.0         0.0         0.0         0.0   
10  CC31_CUMBERLAND         0.0         0.0         0.0         0.0   
11  CC31_CUMBERLAND         0.0         0.0         0.0         0.0   
12     CLEA_SAMPSON         0.0         0.0         0.0         0.0   
13     CLEA_SAMPSON         0.0         0.0         0.0         0.0   
14  CU02_CUMBERLAND         0.0         0.0         0.0         0.0   
15  CU02_CUMBERLAND         0.0         0.0         0.0         0.0   
16   G8A_CUMBERLAND         0.0         0.0         0.0         0.0   
17   G8A_CUMBERLAND         0.0         0.0         0.0         0.0   

    PSL082RMOF PRECINCT      COUNTY            MATCH SLDL_DIST SLDL_DIST_long  \
0         22.0    12-13    CABARRUS   12-13_CABARRUS       082   [SLDL - 082]   
1          0.0    12-13    CABARRUS   12-13_CABARRUS       083   [SLDL - 083]   
2          0.0    15-01        WAKE       15-01_WAKE       033   [SLDL - 033]   
3          0.0    15-01        WAKE       15-01_WAKE       037   [SLDL - 037]   
4          0.0    15-02        WAKE       15-02_WAKE       033   [SLDL - 033]   
5          0.0    15-02        WAKE       15-02_WAKE       036   [SLDL - 036]   
6          0.0    1513B        PITT       1513B_PITT       009   [SLDL - 009]   
7          0.0    1513B        PITT       1513B_PITT       012   [SLDL - 012]   
8          0.0     AH49  CUMBERLAND  AH49_CUMBERLAND       044   [SLDL - 044]   
9          0.0     AH49  CUMBERLAND  AH49_CUMBERLAND       045   [SLDL - 045]   
10         0.0     CC31  CUMBERLAND  CC31_CUMBERLAND       044   [SLDL - 044]   
11         0.0     CC31  CUMBERLAND  CC31_CUMBERLAND       045   [SLDL - 045]   
12         0.0     CLEA     SAMPSON     CLEA_SAMPSON       022   [SLDL - 022]   
13         0.0     CLEA     SAMPSON     CLEA_SAMPSON       021   [SLDL - 021]   
14         0.0     CU02  CUMBERLAND  CU02_CUMBERLAND       044   [SLDL - 044]   
15         0.0     CU02  CUMBERLAND  CU02_CUMBERLAND       045   [SLDL - 045]   
16         0.0      G8A  CUMBERLAND   G8A_CUMBERLAND       044   [SLDL - 044]   
17         0.0      G8A  CUMBERLAND   G8A_CUMBERLAND       045   [SLDL - 045]   

                       UNIQUE_ID  PSL083RPIT  PSL083RWHI  PSL033DGIL  \
0    12-13_CABARRUS [SLDL - 082]         0.0         0.0         0.0   
1    12-13_CABARRUS [SLDL - 083]        15.0        12.0         0.0   
2        15-01_WAKE [SLDL - 033]         0.0         0.0        88.0   
3        15-01_WAKE [SLDL - 037]         0.0         0.0         0.0   
4        15-02_WAKE [SLDL - 033]         0.0         0.0       273.0   
5        15-02_WAKE [SLDL - 036]         0.0         0.0         0.0   
6        1513B_PITT [SLDL - 009]         0.0         0.0         0.0   
7        1513B_PITT [SLDL - 012]         0.0         0.0         0.0   
8   AH49_CUMBERLAND [SLDL - 044]         0.0         0.0         0.0   
9   AH49_CUMBERLAND [SLDL - 045]         0.0         0.0         0.0   
10  CC31_CUMBERLAND [SLDL - 044]         0.0         0.0         0.0   
11  CC31_CUMBERLAND [SLDL - 045]         0.0         0.0         0.0   
12     CLEA_SAMPSON [SLDL - 022]         0.0         0.0         0.0   
13     CLEA_SAMPSON [SLDL - 021]         0.0         0.0         0.0   
14  CU02_CUMBERLAND [SLDL - 044]         0

In [66]:
##CONCAT THE DFS
sldl_final_df = pd.concat([sldl_df_dropped,sldl_precs_split_newgeom])
sldl_final_df['UNIQUE_ID'] = sldl_final_df['UNIQUE_ID'].astype(str)
sldl_final_df = sldl_final_df.fillna(0)
display(sldl_final_df.head())
display(sldl_final_df.tail())

PREC_ID                      ENR_DESC COUNTY_NAM  COUNTY_ID           MATCH  \
0      14           14_Y E SMITH SCHOOL     DURHAM         32       14_DURHAM   
1    EMIS             EMIS_EMERALD ISLE   CARTERET         16   EMIS_CARTERET   
2     131  131_VIENNA ELEMENTARY SCHOOL    FORSYTH         34     131_FORSYTH   
3      MM            MM_MORVEN/MCFARLAN      ANSON          4        MM_ANSON   
4    CRDL                   CRDL_CREDLE  GRANVILLE         39  CRDL_GRANVILLE   

                                            geometry         PREC_CO  \
0  POLYGON ((2043445.004 806092.205, 2043253.389 ...       14_DURHAM   
1  POLYGON ((2566809.355 312013.723, 2567226.337 ...   EMIS_CARTERET   
2  POLYGON ((1580533.350 868933.766, 1580723.583 ...     131_FORSYTH   
3  POLYGON ((1720554.155 385895.605, 1720464.104 ...        MM_ANSON   
4  POLYGON ((2115518.562 932754.945, 2115429.276 ...  CRDL_GRANVILLE   

   PSL003RKOH  PSL003RQUE  PSL003RSMI  PSL003RTYS  PSL005DHUN  PSL005DRIV  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL006RHAN  PSL006RROL  PSL009DFAR  PSL009DHOC  PSL012DBRE  PSL012DBRO  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL012DCOX  PSL014RCLE  PSL014REDW  PSL015RPRI  PSL015RSHE  PSL019DDAW  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL019DMOR  PSL019RMIL  PSL019RPER  PSL020RDAV  PSL020RLAN  PSL021DPEA  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL021DSMI  PSL022DDEN  PSL022DKIR  PSL024DFAR  PSL024DMCN  PSL025RCHE  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL025RMAT  PSL026RTAT  PSL026RWHI  PSL027DHIC  PSL027DMCD  PSL027DWRA  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL033DGIL  PSL033DMAR  PSL035RCAN  PSL035RPET  PSL036RCOL  PSL036RPAG  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0

PREC_ID              ENR_DESC  COUNTY_NAM  COUNTY_ID            MATCH  \
13    CLEA    CLEA_CLINTON, EAST     SAMPSON         82     CLEA_SAMPSON   
14    CU02    CU02_CUMBERLAND #2  CUMBERLAND         26  CU02_CUMBERLAND   
15    CU02    CU02_CUMBERLAND #2  CUMBERLAND         26  CU02_CUMBERLAND   
16     G8A  G8A_CUMBERLAND #4-G8  CUMBERLAND         26   G8A_CUMBERLAND   
17     G8A  G8A_CUMBERLAND #4-G8  CUMBERLAND         26   G8A_CUMBERLAND   

                                             geometry          PREC_CO  \
13  POLYGON ((2202564.917 473728.992, 2202564.917 ...     CLEA_SAMPSON   
14  MULTIPOLYGON (((2008221.765 459424.047, 200822...  CU02_CUMBERLAND   
15  POLYGON ((2014492.174 462676.707, 2014629.679 ...  CU02_CUMBERLAND   
16  MULTIPOLYGON (((2005162.814 458262.364, 200516...   G8A_CUMBERLAND   
17  POLYGON ((2002759.204 455744.707, 2002369.596 ...   G8A_CUMBERLAND   

    PSL003RKOH  PSL003RQUE  PSL003RSMI  PSL003RTYS  PSL005DHUN  PSL005DRIV  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0         0.0         0.0         0.0         0.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PSL006RHAN  PSL006RROL  PSL009DFAR  PSL009DHOC  PSL012DBRE  PSL012DBRO  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0         0.0         0.0         0.0         0.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PSL012DCOX  PSL014RCLE  PSL014REDW  PSL015RPRI  PSL015RSHE  PSL019DDAW  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0         0.0         0.0         0.0         0.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PSL019DMOR  PSL019RMIL  PSL019RPER  PSL020RDAV  PSL020RLAN  PSL021DPEA  \
13         0.0         0.0         0.0         0.0         0.0       158.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0         0.0         0.0         0.0         0.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PSL021DSMI  PSL022DDEN  PSL022DKIR  PSL024DFAR  PSL024DMCN  PSL025RCHE  \
13        57.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0         0.0         0.0         0.0         0.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PSL025RMAT  PSL026RTAT  PSL026RWHI  PSL027DHIC  PSL027DMCD  PSL027DWRA  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0         0.0         0.0         0.0         0.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PSL033DGIL  PSL033DMAR  PSL035RCAN  PSL035RPET  PSL036RCOL  PSL036RPAG  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0   

In [67]:
sldl_final_df['COUNTY_ID'] = sldl_final_df['COUNTY_ID'].astype(str)
sldl_final_df['COUNTYFP'] = sldl_final_df['COUNTY_ID'].apply(lambda x: str(x).zfill(3))
sldl_final_df['UNIQUE_ID'] = sldl_final_df.apply(lambda x: x['MATCH'] if x['UNIQUE_ID']=='nan' else x['UNIQUE_ID'],axis=1)
sldl_final_df.drop(columns = ['PREC_CO','MATCH','PRECINCT','COUNTY','SLDL_DIST_long'],inplace=True)
sldl_final_df_cols = list(sldl_final_df.columns)
sldl_final_df_cols.remove('geometry')
sldl_final_df_cols.remove('SLDL_DIST')
sldl_final_df_cols.remove('UNIQUE_ID')
sldl_final_df_cols.remove('COUNTYFP')
sldl_final_df_cols[0:1] = ['UNIQUE_ID','COUNTYFP']
sldl_final_df_cols[5:5] = ['SLDL_DIST']
sldl_final_df_cols.append('geometry')
sldl_final_df = sldl_final_df[sldl_final_df_cols]
sldl_final_df['SLDL_DIST'] = sldl_final_df['SLDL_DIST'].astype(str)
sldl_final_df['SLDL_DIST'] = sldl_final_df['SLDL_DIST'].apply(lambda x: "n/a" if x in [0,'0'] else x)

display(sldl_final_df.head())
display(sldl_final_df.tail())

UNIQUE_ID COUNTYFP                      ENR_DESC COUNTY_NAM COUNTY_ID  \
0       14_DURHAM      032           14_Y E SMITH SCHOOL     DURHAM        32   
1   EMIS_CARTERET      016             EMIS_EMERALD ISLE   CARTERET        16   
2     131_FORSYTH      034  131_VIENNA ELEMENTARY SCHOOL    FORSYTH        34   
3        MM_ANSON      004            MM_MORVEN/MCFARLAN      ANSON         4   
4  CRDL_GRANVILLE      039                   CRDL_CREDLE  GRANVILLE        39   

  SLDL_DIST  PSL003RKOH  PSL003RQUE  PSL003RSMI  PSL003RTYS  PSL005DHUN  \
0       n/a         0.0         0.0         0.0         0.0         0.0   
1       n/a         0.0         0.0         0.0         0.0         0.0   
2       n/a         0.0         0.0         0.0         0.0         0.0   
3       n/a         0.0         0.0         0.0         0.0         0.0   
4       n/a         0.0         0.0         0.0         0.0         0.0   

   PSL005DRIV  PSL006RHAN  PSL006RROL  PSL009DFAR  PSL009DHOC  PSL012DBRE  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL012DBRO  PSL012DCOX  PSL014RCLE  PSL014REDW  PSL015RPRI  PSL015RSHE  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL019DDAW  PSL019DMOR  PSL019RMIL  PSL019RPER  PSL020RDAV  PSL020RLAN  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL021DPEA  PSL021DSMI  PSL022DDEN  PSL022DKIR  PSL024DFAR  PSL024DMCN  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL025RCHE  PSL025RMAT  PSL026RTAT  PSL026RWHI  PSL027DHIC  PSL027DMCD  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL027DWRA  PSL033DGIL  PSL033DMAR  PSL035RCAN  PSL035RPET  PSL036RCOL  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   PSL036RPAG  PSL037RMOO  PSL037RPAR  PSL037RPOW  PSL038DEDW  PSL038DJON  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0

UNIQUE_ID COUNTYFP              ENR_DESC  COUNTY_NAM  \
13     CLEA_SAMPSON [SLDL - 021]      082    CLEA_CLINTON, EAST     SAMPSON   
14  CU02_CUMBERLAND [SLDL - 044]      026    CU02_CUMBERLAND #2  CUMBERLAND   
15  CU02_CUMBERLAND [SLDL - 045]      026    CU02_CUMBERLAND #2  CUMBERLAND   
16   G8A_CUMBERLAND [SLDL - 044]      026  G8A_CUMBERLAND #4-G8  CUMBERLAND   
17   G8A_CUMBERLAND [SLDL - 045]      026  G8A_CUMBERLAND #4-G8  CUMBERLAND   

   COUNTY_ID SLDL_DIST  PSL003RKOH  PSL003RQUE  PSL003RSMI  PSL003RTYS  \
13        82       021         0.0         0.0         0.0         0.0   
14        26       044         0.0         0.0         0.0         0.0   
15        26       045         0.0         0.0         0.0         0.0   
16        26       044         0.0         0.0         0.0         0.0   
17        26       045         0.0         0.0         0.0         0.0   

    PSL005DHUN  PSL005DRIV  PSL006RHAN  PSL006RROL  PSL009DFAR  PSL009DHOC  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0         0.0         0.0         0.0         0.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PSL012DBRE  PSL012DBRO  PSL012DCOX  PSL014RCLE  PSL014REDW  PSL015RPRI  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0         0.0         0.0         0.0         0.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PSL015RSHE  PSL019DDAW  PSL019DMOR  PSL019RMIL  PSL019RPER  PSL020RDAV  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0         0.0         0.0         0.0         0.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PSL020RLAN  PSL021DPEA  PSL021DSMI  PSL022DDEN  PSL022DKIR  PSL024DFAR  \
13         0.0       158.0        57.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0         0.0         0.0         0.0         0.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PSL024DMCN  PSL025RCHE  PSL025RMAT  PSL026RTAT  PSL026RWHI  PSL027DHIC  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0         0.0         0.0         0.0         0.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PSL027DMCD  PSL027DWRA  PSL033DGIL  PSL033DMAR  PSL035RCAN  PSL035RPET  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0         0.0         0.0   
16         0.0         0.0         0.0         0.0         0.0         0.0   
17         0.0         0.0         0.0         0.0         0.0         0.0   

    PSL036RCOL  PSL036RPAG  PSL037RMOO  PSL037RPAR  PSL037RPOW  PSL038DEDW  \
13         0.0         0.0         0.0         0.0         0.0         0.0   
14         0.0         0.0         0.0         0.0         0.0         0.0   
15         0.0         0.0         0.0         0.0     

In [68]:
sldl_final_df.to_file('./nc_prim_20_sldl_prec.shp')

### Validate election totals

In [69]:
list_of_dfs = [sldu_prec_df,cong_final_df,sldl_final_df]
df_names = ['SLDU','CONG','SLDL']
data_dict = dict(zip(df_names,list_of_dfs))

totals_dict = {}
for df_name,df in data_dict.items():
    col_tots = []
    col_names = []
    for col in df.columns:
        if col.startswith('P'):
            if col.startswith('PREC'):
                continue
            else:
                col_tots.append(int(df[col].sum()))
                col_names.append(col)
    df_dict = dict(zip(col_names,col_tots))
    totals_dict.update({df_name:df_dict})

In [70]:
race_cols = []
race_totals = []
for k,v in totals_dict.items():
    print('***',k,'***')
    for i,j in v.items():
        print(i, '\t', j)
        race_cols.append(i)
        race_totals.append(j)
    print('')
export_dict = {'CANDIDATE':race_cols,'RDH TOTAL': race_totals}
export_dict_df = pd.DataFrame.from_dict(export_dict)
display(export_dict_df.head())

*** SLDU ***
P20AGRDSMI 	 344032
P20AGRDWAD 	 610046
P20AGRDWAT 	 176507
P20ATGRHAY 	 226452
P20ATGRMUM 	 163910
P20ATGRONE 	 338932
P20AUDDTOL 	 257982
P20AUDDWOO 	 896052
P20AUDRHOE 	 296042
P20AUDRSTR 	 380066
P20GOVDBEA 	 219485
P20GOVDCOO 	 1128758
P20GOVDDUY 	 237877
P20GOVDHOL 	 309228
P20GOVDNEW 	 65951
P20GOVDREE 	 167111
P20GOVDTHO 	 220029
P20GOVDTOO 	 111938
P20GOVRBEN 	 20425
P20GOVRCOC 	 48234
P20GOVRELL 	 50526
P20GOVRFOR 	 699219
P20GOVRGEB 	 50472
P20GOVRGRA 	 87009
P20GOVRJOH 	 89195
P20GOVRRIT 	 85023
P20GOVRROB 	 240843
P20GOVRSTO 	 48193
P20GOVRWEL 	 108747
P20INSRCAU 	 449060
P20INSRPIE 	 247129
P20LBRRDOB 	 274953
P20LBRRFLO 	 148707
P20LBRRSTA 	 259387
P20PRECBLA 	 102
P20PRECKRA 	 1199
P20PRECNPR 	 52
P20PREDBEN 	 1977
P20PREDBID 	 572095
P20PREDBLO 	 172512
P20PREDBOO 	 2180
P20PREDBUT 	 43630
P20PREDCAS 	 699
P20PREDDEL 	 1098
P20PREDGAB 	 6621
P20PREDKLO 	 31775
P20PREDNPR 	 11151
P20PREDPAT 	 1341
P20PREDSAN 	 322607
P20PREDSTE 	 10679
P20PREDWAR 	 139901
P

CANDIDATE  RDH TOTAL
0  P20AGRDSMI     344032
1  P20AGRDWAD     610046
2  P20AGRDWAT     176507
3  P20ATGRHAY     226452
4  P20ATGRMUM     163910

In [71]:
export_dict_df.to_csv('./verify_totals2.csv')

In [72]:
non_value_columns = ['UNIQUE_ID','COUNTYFP','ENR_DESC','COUNTY_NAM','COUNTY_ID','SLDL_DIST','geometry']
for index,row in sldl_final_df.iterrows():
    for val in row.index:
        district_assignment = row['SLDL_DIST']
#non_value_columns is a list of the columns that don't contain races
        if val not in non_value_columns and row[val] != 0:
            # In the below [4:6] is where the district assignment is in the string
            if (val[3:6] != district_assignment):
                print("District Assignment: ", str(district_assignment))
                print("Value" , str(val[3:6]))
                print("Column", val)
                print(row["UNIQUE_ID"])
                print(" ")

In [73]:
non_value_columns = ['UNIQUE_ID','COUNTYFP','ENR_DESC','COUNTY_NAM','COUNTY_ID','CONG_DIST','geometry']
for index,row in cong_final_df.iterrows():
    for val in row.index:
        district_assignment = row['CONG_DIST']
#non_value_columns is a list of the columns that don't contain races
        if val not in non_value_columns and row[val] != 0:
            # In the below [4:6] is where the district assignment is in the string
            if (val[4:6] != district_assignment):
                print("District Assignment: ", district_assignment)
                print("Value" , val[4:6])
                print("Column", val)
                print(row["UNIQUE_ID"])
                print(" ")